This notebook allows collecting results across multiple pipeline runs. Concatenating across sessions and bin sizes. 
It takes CSVs, then determines the most recent one from the filename. 

There are two major sets of decoded epochs - Laps and Ripples/Replays
There are two sets of marginals for the decoded epochs - the "by epoch" and "by time bin" marginals.
The "by time bin" epochs are a larger granulation, with each epoch consisting of one or more time bin.


```python

# 2024-01-23 - 
# C:/Users/pho/repos/Spike3DWorkEnv/Spike3D/output/collected_outputs/2024-01-23_GL-fet11-01_12-58-54_time_bin_size_sweep_results.h5
# C:/Users/pho/repos/Spike3DWorkEnv/Spike3D/output/collected_outputs/2024-01-23_GL-11-03_12-3-25_time_bin_size_sweep_results.h5
# C:/Users/pho/repos/Spike3DWorkEnv/Spike3D/output/collected_outputs/2024-01-23_GL-11-02_17-46-44_time_bin_size_sweep_results.h5
# C:/Users/pho/repos/Spike3DWorkEnv/Spike3D/output/collected_outputs/2024-01-23_GL-11-02_19-28-0_time_bin_size_sweep_results.h5
# C:/Users/pho/repos/Spike3DWorkEnv/Spike3D/output/collected_outputs/2024-01-23_GL-2006-4-10_12-58-3_time_bin_size_sweep_results.h5
# C:/Users/pho/repos/Spike3DWorkEnv/Spike3D/output/collected_outputs/2024-01-23_GL-2006-4-10_12-25-50_time_bin_size_sweep_results.h5
# C:/Users/pho/repos/Spike3DWorkEnv/Spike3D/output/collected_outputs/2024-01-23_GL-2006-4-09_16-40-54_time_bin_size_sweep_results.h5
# C:/Users/pho/repos/Spike3DWorkEnv/Spike3D/output/collected_outputs/2024-01-23_GL-2006-6-09_22-24-40_time_bin_size_sweep_results.h5
# C:/Users/pho/repos/Spike3DWorkEnv/Spike3D/output/collected_outputs/2024-01-23_GL-2006-6-12_16-53-46_time_bin_size_sweep_results.h5
# C:/Users/pho/repos/Spike3DWorkEnv/Spike3D/output/collected_outputs/2024-01-23_GL-2006-4-09_17-29-30_time_bin_size_sweep_results.h5
# C:/Users/pho/repos/Spike3DWorkEnv/Spike3D/output/collected_outputs/2024-01-23_GL-2006-6-08_14-26-15_time_bin_size_sweep_results.h5
# C:/Users/pho/repos/Spike3DWorkEnv/Spike3D/output/collected_outputs/2024-01-23_GL-2006-6-09_1-22-43_time_bin_size_sweep_results.h5
# C:/Users/pho/repos/Spike3DWorkEnv/Spike3D/output/collected_outputs/2024-01-23_GL-2006-6-07_16-40-19_time_bin_size_sweep_results.h5
# C:/Users/pho/repos/Spike3DWorkEnv/Spike3D/output/collected_outputs/2024-01-23_GL-2006-6-08_21-16-25_time_bin_size_sweep_results.h5
# C:/Users/pho/repos/Spike3DWorkEnv/Spike3D/output/collected_outputs/2024-01-23_GL-2006-6-12_15-55-31_time_bin_size_sweep_results.h5



# found_session_export_paths = [Path(v).resolve() for v in  ["C:/Users/pho/repos/Spike3DWorkEnv/Spike3D/output/collected_outputs/2024-01-12_0420PM-kdiba_pin01_one_fet11-01_12-58-54-(laps_marginals_df).csv",
# "C:/Users/pho/repos/Spike3DWorkEnv/Spike3D/output/collected_outputs/2024-01-12_0420PM-kdiba_pin01_one_fet11-01_12-58-54-(ripple_marginals_df).csv",
# "C:/Users/pho/repos/Spike3DWorkEnv/Spike3D/output/collected_outputs/2024-01-12_0645PM-kdiba_pin01_one_fet11-01_12-58-54-(laps_marginals_df).csv",
# "C:/Users/pho/repos/Spike3DWorkEnv/Spike3D/output/collected_outputs/2024-01-12_0645PM-kdiba_pin01_one_fet11-01_12-58-54-(ripple_marginals_df).csv",
# "C:/Users/pho/repos/Spike3DWorkEnv/Spike3D/output/collected_outputs/2024-01-12_0828PM-kdiba_pin01_one_fet11-01_12-58-54-(laps_marginals_df).csv",
# "C:/Users/pho/repos/Spike3DWorkEnv/Spike3D/output/collected_outputs/2024-01-12_0828PM-kdiba_pin01_one_fet11-01_12-58-54-(ripple_marginals_df).csv",
# ]]

[
    "2024-02-19_0430PM-kdiba_vvp01_one_2006-4-10_12-25-50-(ripple_simple_pf_pearson_merged_df)_tbin-0.025.csv",
    "2024-02-17_0210AM-kdiba_vvp01_one_2006-4-09_17-29-30-(laps_simple_pf_pearson_merged_df)_tbin-0.025.csv",
    "2024-02-19_0430PM-kdiba_vvp01_one_2006-4-10_12-25-50-(laps_weighted_corr_merged_df)_tbin-0.025.csv",
    "2024-02-19_0430PM-kdiba_vvp01_one_2006-4-10_12-25-50-(ripple_weighted_corr_merged_df)_tbin-0.025.csv",
]

```

In [1]:
%config IPCompleter.use_jedi = False
%pdb off
%load_ext autoreload
%autoreload 3

# required to enable non-blocking interaction:
%gui qt5

import sys
from copy import deepcopy
from typing import Dict, List, Tuple, Optional, Callable, Union, Any
from typing_extensions import TypeAlias
from neuropy.utils.result_context import IdentifyingContext
from nptyping import NDArray
import neuropy.utils.type_aliases as types
from collections import defaultdict

import numpy as np
import pandas as pd
import re
from pathlib import Path
from datetime import datetime

from neuropy.utils.indexing_helpers import PandasHelpers
from pyphocorehelpers.indexing_helpers import partition_df
# Set the maximum number of columns to display
pd.set_option('display.max_columns', 100)

import IPython
from pyphocorehelpers.programming_helpers import IPythonHelpers
from pyphocorehelpers.notebook_helpers import NotebookCellExecutionLogger

_notebook_path:Path = Path(IPythonHelpers.try_find_notebook_filepath(IPython.extract_module_locals())).resolve() # Finds the path of THIS notebook
# _notebook_execution_logger: NotebookCellExecutionLogger = NotebookCellExecutionLogger(notebook_path=_notebook_path, enable_logging_to_file=False) # Builds a logger that records info about this notebook

# Plotting
# import pylustrator # customization of figures
import matplotlib
import matplotlib as mpl
import matplotlib.pyplot as plt
_bak_rcParams = mpl.rcParams.copy()

matplotlib.use('Qt5Agg')
# %matplotlib inline
# %matplotlib auto

# Switch to the desired interactivity mode
plt.interactive(True)

# _restore_previous_matplotlib_settings_callback = matplotlib_configuration_update(is_interactive=True, backend='Qt5Agg')
# _restore_previous_matplotlib_settings_callback = matplotlib_configuration_update(is_interactive=True, backend='Qt5Agg')
import seaborn as sns

import plotly.express as px
import plotly.graph_objects as go
from plotly.subplots import make_subplots
import plotly.io as pio
template: str = 'plotly_dark' # set plotl template
pio.templates.default = template
from pyphocorehelpers.plotting.media_output_helpers import fig_to_clipboard
from pyphocorehelpers.Filesystem.path_helpers import file_uri_from_path, sanitize_filename_for_Windows
from pyphocorehelpers.gui.Jupyter.simple_widgets import fullwidth_path_widget, simple_path_display_widget
from pyphoplacecellanalysis.Pho2D.plotly.Extensions.plotly_helpers import plotly_helper_save_figures, _helper_build_figure, plotly_pre_post_delta_scatter, plot_across_sessions_scatter_results

# from ..PendingNotebookCode import plot_across_sessions_scatter_results, plot_histograms, plot_stacked_histograms
from pyphocorehelpers.Filesystem.path_helpers import find_first_extant_path
from pyphoplacecellanalysis.SpecificResults.AcrossSessionResults import find_csv_files, find_HDF5_files, find_most_recent_files
from pyphoplacecellanalysis.Pho2D.statistics_plotting_helpers import plot_histograms_across_sessions, plot_histograms, plot_stacked_histograms

from pyphoplacecellanalysis.General.Pipeline.Stages.ComputationFunctions.MultiContextComputationFunctions.DirectionalPlacefieldGlobalComputationFunctions import DecoderDecodedEpochsResult
from pyphoplacecellanalysis.SpecificResults.AcrossSessionResults import load_across_sessions_exported_files, _process_and_load_exported_file, _common_cleanup_operations, convert_to_dataframe

from pyphocorehelpers.programming_helpers import metadata_attributes
from pyphocorehelpers.function_helpers import function_attributes

from pyphoplacecellanalysis.SpecificResults.AcrossSessionResults import build_session_t_delta, _new_process_csv_files, _old_process_csv_files

debug_print: bool = False
enable_neptune: bool = False

TODAY_DAY_DATE: str = f"2024-07-15_Apogee"
# TODAY_DAY_DATE: str = f"2024-07-15_GL"
# TODAY_DAY_DATE: str = f"2024-07-15_Lab"
# TODAY_DAY_DATE: str = f"2024-07-15_rMBP"

print(f'TODAY_DAY_DATE: {TODAY_DAY_DATE}')

types.session_str: TypeAlias = str # a unique session identifier

if enable_neptune:
    import neptune # for logging progress and results
    from neptune.types import File
    from pyphoplacecellanalysis.General.Batch.NeptuneAiHelpers import Neptuner, AutoValueConvertingNeptuneRun, set_environment_variables 

    ## Gets the notebook filepath for Neptune:
    import IPython
    from pyphocorehelpers.programming_helpers import IPythonHelpers
    notebook_filepath: str = IPythonHelpers.try_find_notebook_filepath(IPython.extract_module_locals())
    assert Path(notebook_filepath).resolve().exists(), f"found notebook filepath: '{notebook_filepath}' does not exist"
    # notebook_filepath

    neptune_kwargs = {'project':"commander.pho/PhoDibaLongShortAcrossSessions",
    'api_token':"eyJhcGlfYWRkcmVzcyI6Imh0dHBzOi8vYXBwLm5lcHR1bmUuYWkiLCJhcGlfdXJsIjoiaHR0cHM6Ly9hcHAubmVwdHVuZS5haSIsImFwaV9rZXkiOiIxOGIxODU2My1lZTNhLTQ2ZWMtOTkzNS02ZTRmNzM5YmNjNjIifQ=="}
            
    neptuner = Neptuner(project_name=neptune_kwargs['project'], api_token=neptune_kwargs['api_token'])


    if neptuner.run is None:
        neptuner.run = AutoValueConvertingNeptuneRun(project=neptuner.project_name, api_token=neptuner.api_token, dependencies="infer", source_files=[notebook_filepath])
        params = {"TODAY_DAY_DATE": TODAY_DAY_DATE, "run_workstation": "Apogee"}
        neptuner.run["parameters"] = params
        neptuner.outputs = neptuner.run['outputs']
        neptuner.figures = neptuner.outputs['figures']

    neptuner_run: AutoValueConvertingNeptuneRun = neptuner.run
    
    # run = neptune.init_run(source_files=["**/*.dvc"])

    # # Pre-execution dataframe view:
    # run["dataset/global_batch_run_progress_df"].upload(File.as_html(global_batch_run.to_dataframe(expand_context=True, good_only=False))) # "path/to/test_preds.csv"

else:
    # no neptune:
    neptuner = None    
    neptuner_run = None


known_bad_sessions = [IdentifyingContext(format_name='kdiba',animal='pin01',exper_name='one',session_name='11-02_17-46-44')]
known_bad_session_strs = [str(v.get_description()) for v in known_bad_sessions]
known_bad_session_strs

Automatic pdb calling has been turned OFF
TODAY_DAY_DATE: 2024-07-15_Apogee


['kdiba_pin01_one_11-02_17-46-44']

# Definitions
"_new" (as in `all_sessions_new_ripple_df`) adds simple_pearson and a few other measures

### csv_files

In [2]:
## Load across session t_delta CSV, which contains the t_delta for each session:

## INPUTS: known_bad_session_strs,

cuttoff_date = datetime(2024, 7, 11)
# cuttoff_date = datetime(2024, 5, 18)
# cuttoff_date = None

# t_delta_csv_path = Path(r'C:\Users\pho\repos\Spike3DWorkEnv\Spike3D\output\collected_outputs\2024-01-18_GL_t_split_df.csv').resolve() # Apogee
# t_delta_csv_path = Path('/home/halechr/cloud/turbo/Data/Output/collected_outputs/2024-01-18_GL_t_split_df.csv').resolve() # GL

# collected_outputs_directory = '/home/halechr/FastData/collected_outputs/'
# collected_outputs_directory = r'C:\Users\pho\Desktop\collected_outputs'
# collected_outputs_directory = r'C:/Users/pho/repos/Spike3DWorkEnv/Spike3D/output/collected_outputs' # APOGEE
# collected_outputs_directory = '/home/halechr/cloud/turbo/Data/Output/collected_outputs' # GL

known_collected_outputs_paths = [Path(v).resolve() for v in ['/Users/pho/University of Michigan Dropbox/MED-DibaLabDropbox/Data/Pho/Outputs/output/collected_outputs',
                                                            '/Volumes/SwapSSD/Data/collected_outputs', r"K:/scratch/collected_outputs", '/Users/pho/Dropbox (University of Michigan)/MED-DibaLabDropbox/Data/Pho/Outputs/output/collected_outputs', r'C:/Users/pho/repos/Spike3DWorkEnv/Spike3D/output/collected_outputs',
                                                            '/home/halechr/FastData/collected_outputs/', '/home/halechr/cloud/turbo/Data/Output/collected_outputs']]
collected_outputs_directory = find_first_extant_path(known_collected_outputs_paths)
assert collected_outputs_directory.exists(), f"collected_outputs_directory: {collected_outputs_directory} does not exist! Is the right computer's config commented out above?"
# fullwidth_path_widget(scripts_output_path, file_name_label='Scripts Output Path:')
print(f'collected_outputs_directory: {collected_outputs_directory}')

# _active_folder_widget = fullwidth_path_widget(collected_outputs_directory)
# display(_active_folder_widget)

# Create a 'figures' subfolder if it doesn't exist
figures_folder: Path = collected_outputs_directory.joinpath('figures').resolve()
figures_folder.mkdir(parents=False, exist_ok=True)
assert figures_folder.exists()
print(f'\tfigures_folder: {file_uri_from_path(figures_folder)}')

# Create an output path for the across session collected results (like the aggregate CSVs built from the individual session CSVs)
across_sessions_output_folder: Path = collected_outputs_directory.joinpath('../across_sessions').resolve()
across_sessions_output_folder.mkdir(parents=False, exist_ok=True)
assert across_sessions_output_folder.exists()
print(f'\tacross_sessions_output_folder: {file_uri_from_path(across_sessions_output_folder)}')

## sessions' t_delta:
t_delta_csv_path = collected_outputs_directory.joinpath('../2024-01-18_GL_t_split_df.csv').resolve() # GL
# t_delta_csv_path = collected_outputs_directory.joinpath('2024-06-11_GL_t_split_df.csv').resolve()

t_delta_df, t_delta_dict, (earliest_delta_aligned_t_start, latest_delta_aligned_t_end) = build_session_t_delta(t_delta_csv_path=t_delta_csv_path)


if neptuner_run is not None:
    _neptuner_run_parameters = dict(cuttoff_date=cuttoff_date, collected_outputs_directory=collected_outputs_directory.as_posix(), figures_folder=figures_folder.as_posix(),
                           across_sessions_output_folder=across_sessions_output_folder.as_posix(), t_delta_csv_path=t_delta_csv_path.as_posix())
    for k, v in _neptuner_run_parameters.items():
        neptuner_run[f'parameters/{k}'] = v
    _neptuner_run_parameters = {} # reset after writing

## Find the files:
csv_files = find_csv_files(collected_outputs_directory)
h5_files = find_HDF5_files(collected_outputs_directory)

csv_sessions, parsed_csv_files_df  = find_most_recent_files(found_session_export_paths=csv_files, cuttoff_date=cuttoff_date)
h5_sessions, parsed_h5_files_df = find_most_recent_files(found_session_export_paths=h5_files)

## OUTPUTS: csv_files, csv_sessions, parsed_csv_files_df

_neptuner_run_parameters = dict(csv_files=csv_files, h5_files=h5_files, csv_sessions=csv_sessions, h5_sessions=h5_sessions)



# #TODO 2024-03-02 12:12: - [ ] Could add weighted correlation if there is a dataframe for that and it's computed:
_df_raw_variable_names = ['simple_pf_pearson_merged_df', 'weighted_corr_merged_df']
_df_variables_names = ['laps_weighted_corr_merged_df', 'ripple_weighted_corr_merged_df', 'laps_simple_pf_pearson_merged_df', 'ripple_simple_pf_pearson_merged_df']

# # tbin_values_dict = {'laps': self.laps_decoding_time_bin_size, 'ripple': self.ripple_decoding_time_bin_size}
time_col_name_dict = {'laps': 'lap_start_t', 'ripple': 'ripple_start_t'} ## default should be 't_bin_center'

# fold older files:
# {'laps_marginals_df': 'lap_start_t', 'ripple_marginals_df': 'ripple_start_t', 'laps_time_bin_marginals_df':'t_bin_center', 'ripple_time_bin_marginals_df':'t_bin_center'}
    
if neptuner_run is not None:
    _neptuner_run_parameters = _neptuner_run_parameters | dict(earliest_delta_aligned_t_start=earliest_delta_aligned_t_start, latest_delta_aligned_t_end=latest_delta_aligned_t_end,
                                     t_delta_df=t_delta_df)
    for k, v in _neptuner_run_parameters.items():
        neptuner_run[f'parsed/{k}'] = v
    _neptuner_run_parameters = {} # reset after writing


collected_outputs_directory: K:\scratch\collected_outputs
	figures_folder: file:///K:/scratch/collected_outputs/figures
	across_sessions_output_folder: file:///K:/scratch/across_sessions
earliest_delta_aligned_t_start: -2057.2259484970764, latest_delta_aligned_t_end: 1661.8560019930592
ERR: Could not parse filename: "session_h5_files_copydict_2024-06-06_Lab"
ERR: Could not parse filename: "session_h5_files_copydict_2024-06-11_GL"
ERR: Could not parse filename: "session_h5_files_copydict_2024-06-11_Apogee"
ERR: Could not parse filename: "session_h5_files_copydict_2024-06-12_Apogee"
ERR: Could not parse filename: "session_h5_files_copydict_2024-04-27_Apogee"


In [ ]:
parsed_csv_files_df

In [ ]:
parsed_csv_files_df['custom_replay_name'].unique()

In [ ]:

# where is "2024-07-11-kdiba_gor01_one_2006-6-08_14-26-15__withNewKamranExportedReplays-qclu_[1,2]-frateThresh_5.0-(ripple_marginals_df).csv"
[str(v.name) for v in csv_files].index(r"2024-07-11-kdiba_gor01_one_2006-6-08_14-26-15__withNewKamranExportedReplays-qclu_[1,2]-frateThresh_5.0-(ripple_marginals_df).csv")

In [ ]:
[str(v.name) for v in parsed_csv_files_df['path'].to_numpy()].index(r"2024-07-11-kdiba_gor01_one_2006-6-08_14-26-15__withNewKamranExportedReplays-qclu_[1,2]-frateThresh_5.0-(ripple_marginals_df).csv")


In [ ]:
parsed_csv_files_df.iloc[31]

In [ ]:
parsed_csv_files_df[parsed_csv_files_df['path'] == "2024-07-11-kdiba_gor01_one_2006-6-08_14-26-15__withNewKamranExportedReplays-qclu_[1,2]-frateThresh_5.0-(ripple_marginals_df).csv"]


# Continue normal

In [3]:
## NEW `parsed_csv_files_df1-based approach 2024-07-11 - 
## INPUTS: parsed_csv_files_df
dict_results, df_results = _new_process_csv_files(parsed_csv_files_df=parsed_csv_files_df, t_delta_dict=t_delta_dict, cuttoff_date=cuttoff_date, known_bad_session_strs=known_bad_session_strs, debug_print=False) # , known_bad_session_strs=known_bad_session_strs
(final_sessions_loaded_laps_dict, final_sessions_loaded_ripple_dict, final_sessions_loaded_laps_time_bin_dict, final_sessions_loaded_ripple_time_bin_dict, final_sessions_loaded_simple_pearson_laps_dict, final_sessions_loaded_simple_pearson_ripple_dict, final_sessions_loaded_laps_wcorr_dict, final_sessions_loaded_ripple_wcorr_dict, final_sessions_loaded_laps_all_scores_dict, final_sessions_loaded_ripple_all_scores_dict) = dict_results
(all_sessions_laps_df, all_sessions_ripple_df, all_sessions_laps_time_bin_df, all_sessions_ripple_time_bin_df, all_sessions_simple_pearson_laps_df, all_sessions_simple_pearson_ripple_df, all_sessions_wcorr_laps_df, all_sessions_wcorr_ripple_df, all_sessions_all_scores_ripple_df) = df_results

WARN: curr_session_t_delta is None for session_str = "11-02_17-46-44"
File type merged_complete_epoch_stats_df not implemented.
WARN: curr_session_t_delta is None for session_str = "11-02_19-28-0"
File type merged_complete_epoch_stats_df not implemented.
WARN: curr_session_t_delta is None for session_str = "11-03_12-3-25"
File type merged_complete_epoch_stats_df not implemented.
WARN: curr_session_t_delta is None for session_str = "2006-4-09_16-40-54"
File type merged_complete_epoch_stats_df not implemented.
WARN: curr_session_t_delta is None for session_str = "2006-4-09_17-29-30"
File type merged_complete_epoch_stats_df not implemented.
WARN: curr_session_t_delta is None for session_str = "2006-4-10_12-25-50"
File type merged_complete_epoch_stats_df not implemented.
WARN: curr_session_t_delta is None for session_str = "2006-4-10_12-58-3"
File type merged_complete_epoch_stats_df not implemented.
WARN: curr_session_t_delta is None for session_str = "2006-6-07_16-40-19"
File type merged_

In [66]:
all_sessions_all_scores_ripple_df

start         stop  label  duration is_user_annotated_epoch  \
0        40.187177    40.488202      0  0.301025                   False   
1        41.011916    41.359114      1  0.347197                    True   
2        43.429702    43.489729      2  0.060027                   False   
3        44.189868    44.279447      3  0.089579                   False   
4        44.588736    44.829950      4  0.241213                   False   
...            ...          ...    ...       ...                     ...   
24575  3002.376713  3002.690057   1335  0.313344                   False   
24576  3014.881651  3015.465700   1338  0.584048                   False   
24577  3015.760120  3016.156008   1339  0.395888                   False   
24578  3016.796274  3017.078069   1341  0.281794                   False   
24579  3018.429195  3018.755441   1343  0.326246                   False   

      is_valid_epoch      P_LR      P_RL    P_Long   P_Short  P_Long_LR  \
0               True  0.617735  0.382265  0.544716  0.455284   0.336490   
1               True  0.471784  0.528216  0.528794  0.471206   0.249477   
2              False  0.499892  0.500108  0.951851  0.048149   0.475823   
3              False  0.803375  0.196625  0.651744  0.348256   0.523595   
4               True  0.387887  0.612113  0.598822  0.401178   0.232275   
...              ...       ...       ...       ...       ...        ...   
24575          False  0.408064  0.591936  0.413046  0.586954   0.168549   
24576           True  0.446854  0.553146  0.455220  0.544780   0.203417   
24577          False  0.456877  0.543123  0.493579  0.506421   0.225505   
24578           True  0.339241  0.660759  0.421506  0.578494   0.142992   
24579           True  0.360906  0.639094  0.467821  0.532179   0.168839   

       congruent_dir_bins_ratio_long_LR  coverage_long_LR  \
0                              0.363636          0.157895   
1                              0.333333          0.228070   
2                              1.000000          0.105263   
3                              0.500000          0.157895   
4                              0.375000          0.122807   
...                                 ...               ...   
24575                          0.363636          0.293103   
24576                          0.318182          0.344828   
24577                          0.428571          0.310345   
24578                          0.200000          0.310345   
24579                          0.333333          0.344828   

       direction_change_bin_ratio_long_LR  integral_second_derivative_long_LR  \
0                                0.090909                       241946.584175   
1                                0.416667                       472095.808593   
2                                0.000000                            0.000000   
3                                0.000000                           14.387024   
4                                0.250000                       219416.504445   
...                                   ...                                 ...   
24575                            0.545455                       172183.574191   
24576                            0.318182                       139969.479108   
24577                            0.428571                        63039.052818   
24578                            0.200000                       253587.022739   
24579                            0.250000                        49925.596260   

         intercept_long_LR  jump_long_LR  \
0       -868.9289822960824      0.004673   
1        4397.098379877765      0.004673   
2       13429.772137784617      0.000167   
3       247.59017074053855      0.000083   
4      -2297.5986512550976      0.004673   
...                    ...           ...   
24575  -162672.34851390214      0.002951   
24576   -81486.08246718608      0.003443   
24577   32362.305604098852      0.001476   
24578   -944321.8812221211      0.004345   
24579    

In [67]:
all_sessions_ripple_df

P_LR      P_RL    P_Long   P_Short  ripple_idx  ripple_start_t  \
0      0.572743  0.427257  0.589042  0.410958           0       40.187177   
1      0.518085  0.481915  0.527867  0.472133           1       41.011916   
2      0.271274  0.728726  0.465855  0.534145           2       44.588736   
3      0.984812  0.015188  0.841381  0.158619           3       45.379714   
4      0.455694  0.544306  0.804823  0.195177           4       45.994329   
...         ...       ...       ...       ...         ...             ...   
44194  0.514383  0.485617  0.396319  0.603681          90     1429.924337   
44195  0.409463  0.590537  0.331976  0.668024          91     1435.942904   
44196  0.643907  0.356093  0.512303  0.487697          92     1437.783184   
44197  0.652461  0.347539  0.641944  0.358056          93     1445.197729   
44198  0.715728  0.284272  0.473291  0.526709          94     1456.458569   

                             session_name  delta_aligned_start_t  \
0      kdiba_gor01_one_2006-6-08_14-26-15           -1171.370903   
1      kdiba_gor01_one_2006-6-08_14-26-15           -1170.546164   
2      kdiba_gor01_one_2006-6-08_14-26-15           -1166.969344   
3      kdiba_gor01_one_2006-6-08_14-26-15           -1166.178366   
4      kdiba_gor01_one_2006-6-08_14-26-15           -1165.563751   
...                                   ...                    ...   
44194   kdiba_vvp01_two_2006-4-10_12-58-3             497.098131   
44195   kdiba_vvp01_two_2006-4-10_12-58-3             503.116698   
44196   kdiba_vvp01_two_2006-4-10_12-58-3             504.956978   
44197   kdiba_vvp01_two_2006-4-10_12-58-3             512.371523   
44198   kdiba_vvp01_two_2006-4-10_12-58-3             523.632363   

       time_bin_size                                 custom_replay_name  \
0                NaN                                                      
1                NaN                                                      
2                NaN                                                      
3                NaN                                                      
4                NaN                                                      
...              ...                                                ...   
44194            NaN  withNormalComputedReplays-qclu_[1,2]-frateThre...   
44195            NaN  withNormalComputedReplays-qclu_[1,2]-frateThre...   
44196            NaN  withNormalComputedReplays-qclu_[1,2]-frateThre...   
44197            NaN  withNormalComputedReplays-qclu_[1,2]-frateThre...   
44198            NaN  withNormalComputedReplays-qclu_[1,2]-frateThre...   

       epoch_idx  is_valid_epoch  is_user_annotated_epoch  \
0              0            True                    False   
1              1            True                    False   
2              2            True                    False   
3              3            True                    False   
4              4            True                    False   
...          ...             ...                      ...   
44194         90            True                    False   
44195         91            True                    False   
44196         92            True                    False   
44197         93            True                    False   
44198         94            True                    False   

      pre_post_delta_category  
0                   pre-delta  
1                   pre-delta  
2                   pre-delta  
3                   pre-delta  
4                   pre-delta  
...                       ...  
44194              post-delta  
44195              post-delta  
44196              post-delta  
44197              post-delta  
44198              post-delta  

[44199 rows x 14 columns]

In [ ]:
## OLD (pre 2024-07-11):
## INPUTS: csv_sessions
dict_results, df_results = _old_process_csv_files(csv_sessions=csv_sessions, t_delta_dict=t_delta_dict, cuttoff_date=cuttoff_date, known_bad_session_strs=known_bad_session_strs, debug_print=False)
(final_sessions_loaded_laps_dict, final_sessions_loaded_ripple_dict, final_sessions_loaded_laps_time_bin_dict, final_sessions_loaded_ripple_time_bin_dict, final_sessions_loaded_simple_pearson_laps_dict, final_sessions_loaded_simple_pearson_ripple_dict, final_sessions_loaded_laps_wcorr_dict, final_sessions_loaded_ripple_wcorr_dict, final_sessions_loaded_laps_all_scores_dict, final_sessions_loaded_ripple_all_scores_dict) = dict_results
(all_sessions_laps_df, all_sessions_ripple_df, all_sessions_laps_time_bin_df, all_sessions_ripple_time_bin_df, all_sessions_simple_pearson_laps_df, all_sessions_simple_pearson_ripple_df, all_sessions_wcorr_laps_df, all_sessions_wcorr_ripple_df, all_sessions_all_scores_ripple_df) = df_results

In [4]:
all_sessions_ripple_df

P_LR      P_RL    P_Long   P_Short  ripple_idx  ripple_start_t  \
0      0.572743  0.427257  0.589042  0.410958           0       40.187177   
1      0.518085  0.481915  0.527867  0.472133           1       41.011916   
2      0.271274  0.728726  0.465855  0.534145           2       44.588736   
3      0.984812  0.015188  0.841381  0.158619           3       45.379714   
4      0.455694  0.544306  0.804823  0.195177           4       45.994329   
...         ...       ...       ...       ...         ...             ...   
44194  0.514383  0.485617  0.396319  0.603681          90     1429.924337   
44195  0.409463  0.590537  0.331976  0.668024          91     1435.942904   
44196  0.643907  0.356093  0.512303  0.487697          92     1437.783184   
44197  0.652461  0.347539  0.641944  0.358056          93     1445.197729   
44198  0.715728  0.284272  0.473291  0.526709          94     1456.458569   

                             session_name  delta_aligned_start_t  \
0      kdiba_gor01_one_2006-6-08_14-26-15           -1171.370903   
1      kdiba_gor01_one_2006-6-08_14-26-15           -1170.546164   
2      kdiba_gor01_one_2006-6-08_14-26-15           -1166.969344   
3      kdiba_gor01_one_2006-6-08_14-26-15           -1166.178366   
4      kdiba_gor01_one_2006-6-08_14-26-15           -1165.563751   
...                                   ...                    ...   
44194   kdiba_vvp01_two_2006-4-10_12-58-3             497.098131   
44195   kdiba_vvp01_two_2006-4-10_12-58-3             503.116698   
44196   kdiba_vvp01_two_2006-4-10_12-58-3             504.956978   
44197   kdiba_vvp01_two_2006-4-10_12-58-3             512.371523   
44198   kdiba_vvp01_two_2006-4-10_12-58-3             523.632363   

       time_bin_size                                 custom_replay_name  \
0                NaN                                                      
1                NaN                                                      
2                NaN                                                      
3                NaN                                                      
4                NaN                                                      
...              ...                                                ...   
44194            NaN  withNormalComputedReplays-qclu_[1,2]-frateThre...   
44195            NaN  withNormalComputedReplays-qclu_[1,2]-frateThre...   
44196            NaN  withNormalComputedReplays-qclu_[1,2]-frateThre...   
44197            NaN  withNormalComputedReplays-qclu_[1,2]-frateThre...   
44198            NaN  withNormalComputedReplays-qclu_[1,2]-frateThre...   

       epoch_idx  is_valid_epoch  is_user_annotated_epoch  
0              0            True                    False  
1              1            True                    False  
2              2            True                    False  
3              3            True                    False  
4              4            True                    False  
...          ...             ...                      ...  
44194         90            True                    False  
44195         91            True                    False  
44196         92            True                    False  
44197         93            True                    False  
44198         94            True                    False  

[44199 rows x 13 columns]

In [76]:
all_sessions_wcorr_laps_df

P_LR          P_RL        P_Long   P_Short  lap_idx  \
0     7.107682e-01  2.892318e-01  5.870546e-01  0.412945        0   
1     2.716157e-01  7.283843e-01  7.456626e-01  0.254337        1   
2     7.361415e-01  2.638585e-01  6.349346e-01  0.365065        2   
3     2.404260e-01  7.595740e-01  7.879788e-01  0.212021        3   
4     7.294351e-01  2.705649e-01  5.589713e-01  0.441029        4   
...            ...           ...           ...       ...      ...   
9502  3.332293e-01  6.667707e-01  2.516226e-07  1.000000       76   
9503           NaN           NaN           NaN       NaN       77   
9504  2.028781e-01  7.971219e-01  1.342201e-13  1.000000       78   
9505  9.999999e-01  1.265599e-07  5.907929e-31  1.000000       79   
9506  1.646439e-07  9.999998e-01  1.112305e-25  1.000000       80   

      lap_start_t     P_Long_LR     P_Long_RL    P_Short_LR    P_Short_RL  \
0        5.635867  4.172597e-01  1.697949e-01  2.935085e-01  1.194369e-01   
1       31.862536  2.025337e-01  5.431290e-01  6.908202e-02  1.852553e-01   
2      135.801698  4.674017e-01  1.675329e-01  2.687398e-01  9.632561e-02   
3      161.458825  1.894506e-01  5.985282e-01  5.097541e-02  1.610458e-01   
4      234.465983  4.077333e-01  1.512380e-01  3.217018e-01  1.193269e-01   
...           ...           ...           ...           ...           ...   
9502  1354.925739  8.384803e-08  1.677746e-07  3.332292e-01  6.667705e-01   
9503  1371.942384           NaN           NaN           NaN           NaN   
9504  1419.458378  2.723031e-14  1.069898e-13  2.028781e-01  7.971219e-01   
9505  1424.662371  5.907928e-31  7.477069e-38  9.999999e-01  1.265599e-07   
9506  1447.485366  1.831343e-32  1.112305e-25  1.646439e-07  9.999998e-01   

      most_likely_decoder_index  wcorr_long_LR  wcorr_long_RL  wcorr_short_LR  \
0                             0      -0.478555      -0.227398       -0.353855   
1                             1       0.499593       0.667121        0.405739   
2                             0      -0.579911      -0.284048       -0.416294   
3                             1       0.542113       0.730625        0.482056   
4                             0      -0.332784      -0.155286       -0.189347   
...                         ...            ...            ...             ...   
9502                          3       0.536650      -0.999837        0.065764   
9503                          0            NaN            NaN             NaN   
9504                          3      -0.036329       0.327306       -0.962921   
9505                          2       0.998485      -0.287874        0.951838   
9506                          3      -0.999996      -0.999999       -0.808806   

      wcorr_short_RL  best_decoder_index                        session_name  \
0          -0.233255                   0  kdiba_gor01_one_2006-6-08_14-26-15   
1           0.525344                   1  kdiba_gor01_one_2006-6-08_14-26-15   
2          -0.246887                   0  kdiba_gor01_one_2006-6-08_14-26-15   
3           0.595286                   1  kdiba_gor01_one_2006-6-08_14-26-15   
4          -0.124697                   0  kdiba_gor01_one_2006-6-08_14-26-15   
...              ...                 ...                                 ...   
9502       -0.985402                   1   kdiba_vvp01_two_2006-4-10_12-58-3   
9503             NaN                   0   kdiba_vvp01_two_2006-4-10_12-58-3   
9504       -0.997427                   3   kdiba_vvp01_two_2006-4-10_12-58-3   
9505       -0.098696                   0   kdiba_vvp01_two_2006-4-10_12-58-3   
9506       -0.997442                   1   kdiba_vvp01_two_2006-4-10_12-58-3   

      time_bin_size  delta_aligned_start_t  \
0              0.03           -1205.922213   
1              0.03           -1179.695544   
2              0.03           -1075.756382   
3              0.03           -1050.099255   
4              0.03            -977.092097   
...             ...                    ...   
9502

In [54]:
all_sessions_simple_pearson_ripple_df

P_LR      P_RL    P_Long   P_Short  ripple_idx  ripple_start_t  \
0      0.617735  0.382265  0.544716  0.455284           0       40.187177   
1      0.471784  0.528216  0.528794  0.471206           1       41.011916   
2      0.499892  0.500108  0.951851  0.048149           2       43.429702   
3      0.803375  0.196625  0.651744  0.348256           3       44.189868   
4      0.387887  0.612113  0.598822  0.401178           4       44.588736   
...         ...       ...       ...       ...         ...             ...   
37259  0.514383  0.485617  0.396319  0.603681          90     1429.924337   
37260  0.409463  0.590537  0.331976  0.668024          91     1435.942904   
37261  0.643907  0.356093  0.512303  0.487697          92     1437.783184   
37262  0.652461  0.347539  0.641944  0.358056          93     1445.197729   
37263  0.715728  0.284272  0.473291  0.526709          94     1456.458569   

       P_Long_LR  P_Long_RL  P_Short_LR  P_Short_RL  \
0       0.336490   0.208226    0.281245    0.174039   
1       0.249477   0.279317    0.222308    0.248898   
2       0.475823   0.476028    0.024069    0.024080   
3       0.523595   0.128149    0.279780    0.068476   
4       0.232275   0.366547    0.155612    0.245566   
...          ...        ...         ...         ...   
37259   0.203860   0.192459    0.310523    0.293157   
37260   0.135932   0.196044    0.273531    0.394493   
37261   0.329875   0.182427    0.314032    0.173665   
37262   0.418843   0.223101    0.233617    0.124438   
37263   0.338747   0.134544    0.376980    0.149729   

       most_likely_decoder_index        start         stop  label  duration  \
0                              0    40.187177    40.488202    0.0  0.301025   
1                              1    41.011916    41.359114    1.0  0.347197   
2                              1    43.429702    43.489729    2.0  0.060027   
3                              0    44.189868    44.279447    3.0  0.089579   
4                              1    44.588736    44.829950    4.0  0.241213   
...                          ...          ...          ...    ...       ...   
37259                          2  1429.924337  1430.429558   90.0  0.505221   
37260                          3  1435.942904  1436.334707   91.0  0.391803   
37261                          0  1437.783184  1437.959609   92.0  0.176425   
37262                          0  1445.197729  1445.522931   93.0  0.325202   
37263                          2  1456.458569  1456.886960   94.0  0.428390   

       long_LR_pf_peak_x_pearsonr  long_RL_pf_peak_x_pearsonr  \
0                        0.129413                   -0.360773   
1                       -0.041734                   -0.184740   
2                        0.158074                   -0.413563   
3                        0.063765                   -0.587523   
4                       -0.281180                   -0.517863   
...                           ...                         ...   
37259                    0.039529                    0.292715   
37260                   -0.013777                    0.044008   
37261                   -0.771032                   -0.684722   
37262                   -0.539592                   -0.476516   
37263                    0.135099                   -0.142547   

       short_LR_pf_peak_x_pearsonr  short_RL_pf_peak_x_pearsonr  \
0                         0.147619                    -0.272826   
1                        -0.075975                    -0.145443   
2                         0.070741                    -0.471881   
3                        -0.244196                    -0.524257   
4                        -0.230215                    -0.442478   
...                            ...                          ...   
37259                     0.168282                     0.157168   
37260                    -0.058575                     0.148570   
37261                    -0.819549                    -0.910540   
37262                    

In [55]:
all_sessions_all_scores_ripple_df

start         stop  label  duration is_user_annotated_epoch  \
0        40.187177    40.488202      0  0.301025                   False   
1        41.011916    41.359114      1  0.347197                    True   
2        43.429702    43.489729      2  0.060027                   False   
3        44.189868    44.279447      3  0.089579                   False   
4        44.588736    44.829950      4  0.241213                   False   
...            ...          ...    ...       ...                     ...   
24575  3002.376713  3002.690057   1335  0.313344                   False   
24576  3014.881651  3015.465700   1338  0.584048                   False   
24577  3015.760120  3016.156008   1339  0.395888                   False   
24578  3016.796274  3017.078069   1341  0.281794                   False   
24579  3018.429195  3018.755441   1343  0.326246                   False   

      is_valid_epoch      P_LR      P_RL    P_Long   P_Short  P_Long_LR  \
0               True  0.617735  0.382265  0.544716  0.455284   0.336490   
1               True  0.471784  0.528216  0.528794  0.471206   0.249477   
2              False  0.499892  0.500108  0.951851  0.048149   0.475823   
3              False  0.803375  0.196625  0.651744  0.348256   0.523595   
4               True  0.387887  0.612113  0.598822  0.401178   0.232275   
...              ...       ...       ...       ...       ...        ...   
24575          False  0.408064  0.591936  0.413046  0.586954   0.168549   
24576           True  0.446854  0.553146  0.455220  0.544780   0.203417   
24577          False  0.456877  0.543123  0.493579  0.506421   0.225505   
24578           True  0.339241  0.660759  0.421506  0.578494   0.142992   
24579           True  0.360906  0.639094  0.467821  0.532179   0.168839   

       congruent_dir_bins_ratio_long_LR  coverage_long_LR  \
0                              0.363636          0.157895   
1                              0.333333          0.228070   
2                              1.000000          0.105263   
3                              0.500000          0.157895   
4                              0.375000          0.122807   
...                                 ...               ...   
24575                          0.363636          0.293103   
24576                          0.318182          0.344828   
24577                          0.428571          0.310345   
24578                          0.200000          0.310345   
24579                          0.333333          0.344828   

       direction_change_bin_ratio_long_LR  integral_second_derivative_long_LR  \
0                                0.090909                       241946.584175   
1                                0.416667                       472095.808593   
2                                0.000000                            0.000000   
3                                0.000000                           14.387024   
4                                0.250000                       219416.504445   
...                                   ...                                 ...   
24575                            0.545455                       172183.574191   
24576                            0.318182                       139969.479108   
24577                            0.428571                        63039.052818   
24578                            0.200000                       253587.022739   
24579                            0.250000                        49925.596260   

         intercept_long_LR  jump_long_LR  \
0       -868.9289822960824      0.004673   
1        4397.098379877765      0.004673   
2       13429.772137784617      0.000167   
3       247.59017074053855      0.000083   
4      -2297.5986512550976      0.004673   
...                    ...           ...   
24575  -162672.34851390214      0.002951   
24576   -81486.08246718608      0.003443   
24577   32362.305604098852      0.001476   
24578   -944321.8812221211      0.004345   
24579    

In [77]:
## filter by specific set of replays:
# dfs_list = (all_sessions_ripple_df, all_sessions_ripple_time_bin_df, all_sessions_simple_pearson_ripple_df, all_sessions_wcorr_ripple_df, all_sessions_all_scores_ripple_df)

replay_name: str = 'withNewComputedReplays-qclu_[1, 2]-frateThresh_5.0'
time_bin_size: float = 0.02
filtered_all_sessions_ripple_df = deepcopy(all_sessions_ripple_df)[(all_sessions_ripple_df['custom_replay_name'] == replay_name) & (all_sessions_ripple_df['time_bin_size'] == time_bin_size)]
filtered_all_sessions_ripple_time_bin_df = deepcopy(all_sessions_ripple_time_bin_df)[(all_sessions_ripple_time_bin_df['custom_replay_name'] == replay_name) & (all_sessions_ripple_time_bin_df['time_bin_size'] == time_bin_size)]
filtered_all_sessions_simple_pearson_ripple_df = deepcopy(all_sessions_simple_pearson_ripple_df)[(all_sessions_simple_pearson_ripple_df['custom_replay_name'] == replay_name) & (all_sessions_simple_pearson_ripple_df['time_bin_size'] == time_bin_size)]
filtered_all_sessions_wcorr_ripple_df = deepcopy(all_sessions_wcorr_ripple_df)[(all_sessions_wcorr_ripple_df['custom_replay_name'] == replay_name) & (all_sessions_wcorr_ripple_df['time_bin_size'] == time_bin_size)]
## OUTPUTS: filtered_all_sessions_ripple_df, filtered_all_sessions_ripple_time_bin_df, filtered_all_sessions_simple_pearson_ripple_df, filtered_all_sessions_wcorr_ripple_df

In [56]:
all_sessions_ripple_df['custom_replay_name'].unique()

array(['', 'withOldestImportedReplays-qclu_XX-frateThresh_0.1',
       'withNewComputedReplays-qclu_[1, 2]-frateThresh_5.0',
       'withNewKamranExportedReplays-qclu_[1,2]-frateThresh_5.0',
       'withNormalComputedReplays-qclu_[1,2]-frateThresh_1.0'],
      dtype=object)

In [57]:
all_sessions_ripple_time_bin_df['custom_replay_name'].unique()

array(['', 'withOldestImportedReplays-qclu_XX-frateThresh_0.1',
       'withNewComputedReplays-qclu_[1, 2]-frateThresh_5.0',
       'withNewKamranExportedReplays-qclu_[1,2]-frateThresh_5.0',
       'withNormalComputedReplays-qclu_[1,2]-frateThresh_1.0'],
      dtype=object)

In [58]:
all_sessions_simple_pearson_ripple_df['custom_replay_name'].unique()

array(['', 'withOldestImportedReplays-qclu_XX-frateThresh_0.1',
       'withNewComputedReplays-qclu_[1, 2]-frateThresh_5.0',
       'withNewKamranExportedReplays-qclu_[1,2]-frateThresh_5.0',
       'withNormalComputedReplays-qclu_[1,2]-frateThresh_1.0'],
      dtype=object)

In [59]:
all_sessions_wcorr_ripple_df['custom_replay_name'].unique() 

# ['', 'withOldestImportedReplays-qclu_XX-frateThresh_0.1',
# 'withNewComputedReplays-qclu_[1, 2]-frateThresh_5.0',
# 'withNewKamranExportedReplays-qclu_[1,2]-frateThresh_5.0',
# 'withNormalComputedReplays-qclu_[1,2]-frateThresh_1.0']



array(['', 'withOldestImportedReplays-qclu_XX-frateThresh_0.1',
       'withNewComputedReplays-qclu_[1, 2]-frateThresh_5.0',
       'withNewKamranExportedReplays-qclu_[1,2]-frateThresh_5.0',
       'withNormalComputedReplays-qclu_[1,2]-frateThresh_1.0'],
      dtype=object)

In [60]:
all_sessions_all_scores_ripple_df['custom_replay_name'].unique() ## OH no, only this one is missing values

array([''], dtype=object)

In [70]:
# Sort by columns: 'session' (ascending), 'custom_replay_name' (ascending) and 3 other columns
parsed_csv_files_df = parsed_csv_files_df.sort_values(['session', 'file_type', 'custom_replay_name', 'decoding_time_bin_size_str', 'export_datetime']).reset_index(drop=True)
parsed_csv_files_df

export_datetime                            session  \
0   2024-07-12 00:00:00                     11-02_17-46-44   
1   2024-07-12 00:00:00                      11-02_19-28-0   
2   2024-07-12 00:00:00                      11-03_12-3-25   
3   2024-07-12 00:00:00                 2006-4-09_16-40-54   
4   2024-07-12 00:00:00                 2006-4-09_17-29-30   
..                  ...                                ...   
951 2024-07-12 16:30:00  kdiba_vvp01_two_2006-4-10_12-58-3   
952 2024-07-12 16:40:00  kdiba_vvp01_two_2006-4-10_12-58-3   
953 2024-07-12 16:40:00  kdiba_vvp01_two_2006-4-10_12-58-3   
954 2024-07-12 16:30:00  kdiba_vvp01_two_2006-4-10_12-58-3   
955 2024-07-12 16:30:00  kdiba_vvp01_two_2006-4-10_12-58-3   

                                    custom_replay_name  \
0                                                        
1                                                        
2                                                        
3                                                        
4                                                        
..                                                 ...   
951  withNewComputedReplays-qclu_[1, 2]-frateThresh...   
952  withNewKamranExportedReplays-qclu_[1,2]-frateT...   
953  withNewKamranExportedReplays-qclu_[1,2]-frateT...   
954  withNormalComputedReplays-qclu_[1,2]-frateThre...   
955  withNormalComputedReplays-qclu_[1,2]-frateThre...   

                          file_type decoding_time_bin_size_str  \
0    merged_complete_epoch_stats_df                              
1    merged_complete_epoch_stats_df                              
2    merged_complete_epoch_stats_df                              
3    merged_complete_epoch_stats_df                              
4    merged_complete_epoch_stats_df                              
..                              ...                        ...   
951  ripple_weighted_corr_merged_df                       0.02   
952  ripple_weighted_corr_merged_df                       0.01   
953  ripple_weighted_corr_merged_df                       0.02   
954  ripple_weighted_corr_merged_df                       0.01   
955  ripple_weighted_corr_merged_df                       0.02   

                                                  path  
0    K:\scratch\collected_outputs\2024-07-12_GL-11-...  
1    K:\scratch\collected_outputs\2024-07-12_GL-11-...  
2    K:\scratch\collected_outputs\2024-07-12_GL-11-...  
3    K:\scratch\collected_outputs\2024-07-12_GL-200...  
4    K:\scratch\collected_outputs\2024-07-12_GL-200...  
..                                                 ...  
951  K:\scratch\collected_outputs\2024-07-12_0430PM...  
952  K:\scratch\collected_outputs\2024-07-12_0440PM...  
953  K:\scratch\collected_outputs\2024-07-12_0440PM...  
954  K:\scratch\collected_outputs\2024-07-12_0430PM...  
955  K:\scratch\collected_outputs\2024-07-12_0430PM...  

[956 rows x 6 columns]

In [71]:
all_sessions_ripple_df

P_LR      P_RL    P_Long   P_Short  ripple_idx  ripple_start_t  \
0      0.572743  0.427257  0.589042  0.410958           0       40.187177   
1      0.518085  0.481915  0.527867  0.472133           1       41.011916   
2      0.271274  0.728726  0.465855  0.534145           2       44.588736   
3      0.984812  0.015188  0.841381  0.158619           3       45.379714   
4      0.455694  0.544306  0.804823  0.195177           4       45.994329   
...         ...       ...       ...       ...         ...             ...   
44194  0.514383  0.485617  0.396319  0.603681          90     1429.924337   
44195  0.409463  0.590537  0.331976  0.668024          91     1435.942904   
44196  0.643907  0.356093  0.512303  0.487697          92     1437.783184   
44197  0.652461  0.347539  0.641944  0.358056          93     1445.197729   
44198  0.715728  0.284272  0.473291  0.526709          94     1456.458569   

                             session_name  delta_aligned_start_t  \
0      kdiba_gor01_one_2006-6-08_14-26-15           -1171.370903   
1      kdiba_gor01_one_2006-6-08_14-26-15           -1170.546164   
2      kdiba_gor01_one_2006-6-08_14-26-15           -1166.969344   
3      kdiba_gor01_one_2006-6-08_14-26-15           -1166.178366   
4      kdiba_gor01_one_2006-6-08_14-26-15           -1165.563751   
...                                   ...                    ...   
44194   kdiba_vvp01_two_2006-4-10_12-58-3             497.098131   
44195   kdiba_vvp01_two_2006-4-10_12-58-3             503.116698   
44196   kdiba_vvp01_two_2006-4-10_12-58-3             504.956978   
44197   kdiba_vvp01_two_2006-4-10_12-58-3             512.371523   
44198   kdiba_vvp01_two_2006-4-10_12-58-3             523.632363   

       time_bin_size                                 custom_replay_name  \
0                NaN                                                      
1                NaN                                                      
2                NaN                                                      
3                NaN                                                      
4                NaN                                                      
...              ...                                                ...   
44194            NaN  withNormalComputedReplays-qclu_[1,2]-frateThre...   
44195            NaN  withNormalComputedReplays-qclu_[1,2]-frateThre...   
44196            NaN  withNormalComputedReplays-qclu_[1,2]-frateThre...   
44197            NaN  withNormalComputedReplays-qclu_[1,2]-frateThre...   
44198            NaN  withNormalComputedReplays-qclu_[1,2]-frateThre...   

       epoch_idx  is_valid_epoch  is_user_annotated_epoch  \
0              0            True                    False   
1              1            True                    False   
2              2            True                    False   
3              3            True                    False   
4              4            True                    False   
...          ...             ...                      ...   
44194         90            True                    False   
44195         91            True                    False   
44196         92            True                    False   
44197         93            True                    False   
44198         94            True                    False   

      pre_post_delta_category  
0                   pre-delta  
1                   pre-delta  
2                   pre-delta  
3                   pre-delta  
4                   pre-delta  
...                       ...  
44194              post-delta  
44195              post-delta  
44196              post-delta  
44197              post-delta  
44198              post-delta  

[44199 rows x 14 columns]

In [ ]:
# sess_names, replay_names = all_sessions_ripple_df['session_name'].str.split('__') # , maxsplit=1

for a_split in all_sessions_ripple_df['session_name'].str.split('__'):
	print(f'a_split: {a_split}')

	if len(a_split) > 1:
		print(f'a_split: {a_split}')


In [ ]:
all_sessions_ripple_time_bin_df['custom_replay_name'].unique()
# all_sessions_ripple_df['custom_replay_name'].unique()

In [ ]:
# pd.set_option('display.min_rows', 50)
# pd.set_option('display.max_rows', 50)
# pd.set_option('display.show_dimensions', True)

with pd.option_context('display.min_rows', 50, 'display.show_dimensions', True):
    # max_elements
    display(parsed_csv_files_df)

# parsed_csv_files_df[parsed_csv_files_df['file_type'] == 'ripple_all_scores_merged_df']


In [ ]:
parsed_csv_files_df[parsed_csv_files_df['file_type'] == 'ripple_all_scores_merged_df']

# all_sessions_all_scores_ripple_df


In [7]:
all_sessions_ripple_time_bin_df

P_LR          P_RL    P_Long   P_Short  epoch_idx  t_bin_center  \
0       0.026580  9.734196e-01  0.589377  0.410623          0     40.202177   
1       0.096444  9.035562e-01  0.794633  0.205367          0     40.232177   
2       0.813426  1.865735e-01  0.420990  0.579010          0     40.262177   
3       1.000000  1.617739e-07  0.996191  0.003809          0     40.292177   
4       0.616201  3.837986e-01  0.867583  0.132417          0     40.322177   
...          ...           ...       ...       ...        ...           ...   
404173  0.835499  1.645006e-01  0.527145  0.472855         94   1456.788569   
404174  0.510939  4.890609e-01  0.432948  0.567052         94   1456.808569   
404175  0.742843  2.571566e-01  0.288136  0.711864         94   1456.828569   
404176  0.510939  4.890609e-01  0.432948  0.567052         94   1456.848569   
404177  0.952987  4.701313e-02  0.467316  0.532684         94   1456.868569   

                              session_name  delta_aligned_start_t  \
0       kdiba_gor01_one_2006-6-08_14-26-15           -1171.355903   
1       kdiba_gor01_one_2006-6-08_14-26-15           -1171.325903   
2       kdiba_gor01_one_2006-6-08_14-26-15           -1171.295903   
3       kdiba_gor01_one_2006-6-08_14-26-15           -1171.265903   
4       kdiba_gor01_one_2006-6-08_14-26-15           -1171.235903   
...                                    ...                    ...   
404173   kdiba_vvp01_two_2006-4-10_12-58-3             523.962363   
404174   kdiba_vvp01_two_2006-4-10_12-58-3             523.982363   
404175   kdiba_vvp01_two_2006-4-10_12-58-3             524.002363   
404176   kdiba_vvp01_two_2006-4-10_12-58-3             524.022363   
404177   kdiba_vvp01_two_2006-4-10_12-58-3             524.042363   

        time_bin_size                                 custom_replay_name  
0                 NaN                                                     
1                 NaN                                                     
2                 NaN                                                     
3                 NaN                                                     
4                 NaN                                                     
...               ...                                                ...  
404173            NaN  withNormalComputedReplays-qclu_[1,2]-frateThre...  
404174            NaN  withNormalComputedReplays-qclu_[1,2]-frateThre...  
404175            NaN  withNormalComputedReplays-qclu_[1,2]-frateThre...  
404176            NaN  withNormalComputedReplays-qclu_[1,2]-frateThre...  
404177            NaN  withNormalComputedReplays-qclu_[1,2]-frateThre...  

[404178 rows x 10 columns]

In [ ]:
print(list(np.unique(parsed_csv_files_df.file_type))) # ['laps_marginals_df', 'laps_simple_pf_pearson_merged_df', 'laps_time_bin_marginals_df', 'laps_weighted_corr_merged_df', 'merged_complete_epoch_stats_df', 'ripple_all_scores_merged_df', 'ripple_marginals_df', 'ripple_simple_pf_pearson_merged_df', 'ripple_time_bin_marginals_df', 'ripple_weighted_corr_merged_df']

In [ ]:
csv_sessions

In [8]:
display(parsed_csv_files_df)

across_sessions_parsed_csv_files_path = across_sessions_output_folder.joinpath(f'{TODAY_DAY_DATE}_parsed_csv_files_df.csv').resolve()
# parsed_csv_files_df.to_clipboard(excel=True)
parsed_csv_files_df.to_csv(across_sessions_parsed_csv_files_path)
display(fullwidth_path_widget(across_sessions_parsed_csv_files_path, file_name_label='across_sessions_parsed_csv_files_path:'))

export_datetime                            session  \
0   2024-07-12 00:00:00                     11-02_17-46-44   
1   2024-07-12 00:00:00                      11-02_19-28-0   
2   2024-07-12 00:00:00                      11-03_12-3-25   
3   2024-07-12 00:00:00                 2006-4-09_16-40-54   
4   2024-07-12 00:00:00                 2006-4-09_17-29-30   
..                  ...                                ...   
951 2024-07-12 16:30:00  kdiba_vvp01_two_2006-4-10_12-58-3   
952 2024-07-12 16:40:00  kdiba_vvp01_two_2006-4-10_12-58-3   
953 2024-07-12 16:40:00  kdiba_vvp01_two_2006-4-10_12-58-3   
954 2024-07-12 16:30:00  kdiba_vvp01_two_2006-4-10_12-58-3   
955 2024-07-12 16:30:00  kdiba_vvp01_two_2006-4-10_12-58-3   

                                    custom_replay_name  \
0                                                        
1                                                        
2                                                        
3                                                        
4                                                        
..                                                 ...   
951  withNewComputedReplays-qclu_[1, 2]-frateThresh...   
952  withNewKamranExportedReplays-qclu_[1,2]-frateT...   
953  withNewKamranExportedReplays-qclu_[1,2]-frateT...   
954  withNormalComputedReplays-qclu_[1,2]-frateThre...   
955  withNormalComputedReplays-qclu_[1,2]-frateThre...   

                          file_type decoding_time_bin_size_str  \
0    merged_complete_epoch_stats_df                              
1    merged_complete_epoch_stats_df                              
2    merged_complete_epoch_stats_df                              
3    merged_complete_epoch_stats_df                              
4    merged_complete_epoch_stats_df                              
..                              ...                        ...   
951  ripple_weighted_corr_merged_df                       0.02   
952  ripple_weighted_corr_merged_df                       0.01   
953  ripple_weighted_corr_merged_df                       0.02   
954  ripple_weighted_corr_merged_df                       0.01   
955  ripple_weighted_corr_merged_df                       0.02   

                                                  path  
0    K:\scratch\collected_outputs\2024-07-12_GL-11-...  
1    K:\scratch\collected_outputs\2024-07-12_GL-11-...  
2    K:\scratch\collected_outputs\2024-07-12_GL-11-...  
3    K:\scratch\collected_outputs\2024-07-12_GL-200...  
4    K:\scratch\collected_outputs\2024-07-12_GL-200...  
..                                                 ...  
951  K:\scratch\collected_outputs\2024-07-12_0430PM...  
952  K:\scratch\collected_outputs\2024-07-12_0440PM...  
953  K:\scratch\collected_outputs\2024-07-12_0440PM...  
954  K:\scratch\collected_outputs\2024-07-12_0430PM...  
955  K:\scratch\collected_outputs\2024-07-12_0430PM...  

[956 rows x 6 columns]

Box(children=(Label(value='across_sessions_parsed_csv_files_path:', layout=Layout(width='auto')), HTML(value="…

In [9]:
from pyphoplacecellanalysis.SpecificResults.AcrossSessionResults import export_across_session_CSVs

final_across_session_summary_CSVs_output_path = across_sessions_output_folder.resolve()
display(fullwidth_path_widget(final_across_session_summary_CSVs_output_path, file_name_label='final_across_session_summary_CSVs_output_path:'))
final_csv_export_paths = export_across_session_CSVs(final_output_path=final_across_session_summary_CSVs_output_path, TODAY_DAY_DATE=TODAY_DAY_DATE,
                                                    all_sessions_laps_df=all_sessions_laps_df,  all_sessions_ripple_df=all_sessions_ripple_df,  all_sessions_laps_time_bin_df=all_sessions_laps_time_bin_df,  all_sessions_ripple_time_bin_df=all_sessions_ripple_time_bin_df, 
                                                    all_sessions_simple_pearson_laps_df=all_sessions_simple_pearson_laps_df,  all_sessions_simple_pearson_ripple_df=all_sessions_simple_pearson_ripple_df,
                                                    all_sessions_all_scores_ripple_df=all_sessions_all_scores_ripple_df,  all_sessions_all_scores_laps_df=None,
                                                )

# final_csv_export_paths: {'AcrossSession_Laps_per-Epoch': WindowsPath('K:/scratch/across_sessions/2024-06-05_Apogee_AcrossSession_Laps_per-Epoch.csv'),
#  'AcrossSession_Ripple_per-Epoch': WindowsPath('K:/scratch/across_sessions/2024-06-05_Apogee_AcrossSession_Ripple_per-Epoch.csv'),
#  'AcrossSession_Laps_per-TimeBin': WindowsPath('K:/scratch/across_sessions/2024-06-05_Apogee_AcrossSession_Laps_per-TimeBin.csv'),
#  'AcrossSession_Ripple_per-TimeBin': WindowsPath('K:/scratch/across_sessions/2024-06-05_Apogee_AcrossSession_Ripple_per-TimeBin.csv'),
#  'AcrossSession_SimplePearson_Laps_per-Epoch': WindowsPath('K:/scratch/across_sessions/2024-06-05_Apogee_AcrossSession_SimplePearson_Laps_per-Epoch.csv'),
#  'AcrossSession_SimplePearson_Ripple_per-Epoch': WindowsPath('K:/scratch/across_sessions/2024-06-05_Apogee_AcrossSession_SimplePearson_Ripple_per-Epoch.csv'),
#  'AcrossSession_AllScores_Ripple_per-Epoch': WindowsPath('K:/scratch/across_sessions/2024-06-05_Apogee_AcrossSession_AllScores_Ripple_per-Epoch.csv')}

if neptuner_run is not None:
    _neptuner_run_parameters = dict(across_sessions_parsed_csv_files_path=across_sessions_parsed_csv_files_path.as_posix(), final_across_session_summary_CSVs_output_path=final_across_session_summary_CSVs_output_path.as_posix(),
                                       )
    for k, v in _neptuner_run_parameters.items():
        neptuner_run[f'output_files/{k}'] = v
    _neptuner_run_parameters = {} # reset after writing

    for k, v in final_csv_export_paths.items():
        neptuner_run[f"output_files/{k}"].upload(v.resolve().as_posix())
        

final_csv_export_paths

Box(children=(Label(value='final_across_session_summary_CSVs_output_path:', layout=Layout(width='auto')), HTML…

{'AcrossSession_Laps_per-Epoch': WindowsPath('K:/scratch/across_sessions/2024-07-15_Apogee_AcrossSession_Laps_per-Epoch.csv'),
 'AcrossSession_Ripple_per-Epoch': WindowsPath('K:/scratch/across_sessions/2024-07-15_Apogee_AcrossSession_Ripple_per-Epoch.csv'),
 'AcrossSession_Laps_per-TimeBin': WindowsPath('K:/scratch/across_sessions/2024-07-15_Apogee_AcrossSession_Laps_per-TimeBin.csv'),
 'AcrossSession_Ripple_per-TimeBin': WindowsPath('K:/scratch/across_sessions/2024-07-15_Apogee_AcrossSession_Ripple_per-TimeBin.csv'),
 'AcrossSession_SimplePearson_Laps_per-Epoch': WindowsPath('K:/scratch/across_sessions/2024-07-15_Apogee_AcrossSession_SimplePearson_Laps_per-Epoch.csv'),
 'AcrossSession_SimplePearson_Ripple_per-Epoch': WindowsPath('K:/scratch/across_sessions/2024-07-15_Apogee_AcrossSession_SimplePearson_Ripple_per-Epoch.csv'),
 'AcrossSession_AllScores_Ripple_per-Epoch': WindowsPath('K:/scratch/across_sessions/2024-07-15_Apogee_AcrossSession_AllScores_Ripple_per-Epoch.csv')}

### h5_files

In [ ]:
from pyphoplacecellanalysis.SpecificResults.AcrossSessionResults import load_across_sessions_exported_h5_files

## INPUTS: h5_sessions, session_dict, cuttoff_date, known_bad_session_strs
parsed_h5_files_df, h5_contexts_paths_dict = load_across_sessions_exported_h5_files(collected_outputs_directory=collected_outputs_directory, cuttoff_date=cuttoff_date,
                                                                                    known_bad_session_strs=known_bad_session_strs)
h5_session_contexts = list(h5_contexts_paths_dict.keys())
included_h5_paths = list(h5_contexts_paths_dict.values())

if neptuner_run is not None:
    _neptuner_run_parameters = dict(parsed_h5_files_df=parsed_h5_files_df,
                                       )
    for k, v in _neptuner_run_parameters.items():
        neptuner_run[f'parsed/{k}'] = v
    _neptuner_run_parameters = {} # reset after writing

parsed_h5_files_df
# h5_contexts_paths_dict


In [ ]:
from pyphoplacecellanalysis.SpecificResults.AcrossSessionResults import AcrossSessionTables
from pyphoplacecellanalysis.SpecificResults.AcrossSessionResults import AcrossSessionsVisualizations

included_session_contexts = deepcopy(h5_session_contexts)
included_h5_paths = deepcopy(included_h5_paths)
num_sessions = len(included_session_contexts)
(neuron_identities_table, long_short_fr_indicies_analysis_table, neuron_replay_stats_table), output_path_dicts = AcrossSessionTables.build_and_save_all_combined_tables(included_session_contexts, included_h5_paths,
                                                                                                                                                    override_output_parent_path=across_sessions_output_folder, output_path_suffix=f'{TODAY_DAY_DATE}',
                                                                                                                                                    should_restore_native_column_types=True, include_csv=True, include_pkl=True)


if neptuner_run is not None:
    _neptuner_run_parameters = dict(neuron_identities_table=neuron_identities_table, long_short_fr_indicies_analysis_table=long_short_fr_indicies_analysis_table, neuron_replay_stats_table=neuron_replay_stats_table,
                                       num_sessions=num_sessions)
    for k, v in _neptuner_run_parameters.items():
        neptuner_run[f'parsed/{k}'] = v
    _neptuner_run_parameters = {} # reset after writing

    for output_name, a_paths_dict in output_path_dicts.items():
        for format_extension, an_output_path in a_paths_dict.items():
            neptuner_run[f"output_files/{format_extension}/{output_name}"].upload(an_output_path.resolve().as_posix())


# {'neuron_identities_table': {'.csv': WindowsPath('K:/scratch/across_sessions/2024-06-05_Apogee/neuron_identities_table.csv'),
#   '.pkl': WindowsPath('K:/scratch/across_sessions/2024-06-05_Apogee/neuron_identities_table.pkl')},
#  'long_short_fr_indicies_analysis_table': {'.csv': WindowsPath('K:/scratch/across_sessions/2024-06-05_Apogee/long_short_fr_indicies_analysis_table.csv'),
#   '.pkl': WindowsPath('K:/scratch/across_sessions/2024-06-05_Apogee/long_short_fr_indicies_analysis_table.pkl')},
#  'neuron_replay_stats_table': {'.csv': WindowsPath('K:/scratch/across_sessions/2024-06-05_Apogee/neuron_replay_stats_table.csv'),
#   '.pkl': WindowsPath('K:/scratch/across_sessions/2024-06-05_Apogee/neuron_replay_stats_table.pkl')}}

output_path_dicts

In [ ]:
neuron_identities_table

In [ ]:
neuron_replay_stats_table

In [ ]:
long_short_fr_indicies_analysis_table

In [ ]:
print(list(neuron_replay_stats_table.columns))


In [ ]:
from pyphocorehelpers.indexing_helpers import reorder_columns, reorder_columns_relative

## Move the "height" columns to the end
# _neuron_columns_order_dict = dict(zip(['neuron_uid', 'format_name', 'animal', 'exper_name', 'session_name', 'neuron_type', 'aclu', 'session_uid', 'session_datetime'], np.arange(4)+4))

# neuron_replay_stats_table = reorder_columns_relative(neuron_replay_stats_table, column_names=['neuron_uid', 'format_name', 'animal', 'exper_name', 'session_name', 'neuron_type', 'aclu', 'session_uid', 'session_datetime'],
#                                                     relative_mode='end')
neuron_replay_stats_table = reorder_columns_relative(neuron_replay_stats_table, column_names=['neuron_uid', 'format_name', 'animal', 'exper_name', 'session_name', 'neuron_type', 'aclu', 'session_uid', 'session_datetime'],
                                                    relative_mode='start')

neuron_replay_stats_table


In [ ]:
from pyphoplacecellanalysis.SpecificResults.AcrossSessionResults import AcrossSessionsResults

# matplotlib_configuration_update(is_interactive=True, backend='Qt5Agg')

AcrossSessionsResults.post_compute_all_sessions_processing(global_data_root_parent_path=collected_outputs_directory, BATCH_DATE_TO_USE=TODAY_DAY_DATE, plotting_enabled=True)

In [ ]:
global_multi_session_context, _out_aggregate_fig_2 = AcrossSessionsVisualizations.across_sessions_bar_graphs(across_session_inst_fr_computation, num_sessions, enable_tiny_point_labels=False, enable_hover_labels=False)

In [ ]:
graphics_output_dict = AcrossSessionsVisualizations.across_sessions_firing_rate_index_figure(long_short_fr_indicies_analysis_results=long_short_fr_indicies_analysis_table, num_sessions=num_sessions) ## WORKS


In [ ]:
print(list(all_sessions_all_scores_ripple_df.columns)) # ['start', 'stop', 'label', 'duration', 'is_user_annotated_epoch', 'is_valid_epoch', 'P_LR', 'P_RL', 'P_Long', 'P_Short', 'P_Long_LR', 'score_long_LR', 'velocity_long_LR', 'intercept_long_LR', 'speed_long_LR', 'wcorr_long_LR', 'pearsonr_long_LR', 'travel_long_LR', 'coverage_long_LR', 'jump_long_LR', 'longest_sequence_length_ratio_long_LR', 'direction_change_bin_ratio_long_LR', 'congruent_dir_bins_ratio_long_LR', 'total_congruent_direction_change_long_LR', 'P_Long_RL', 'score_long_RL', 'velocity_long_RL', 'intercept_long_RL', 'speed_long_RL', 'wcorr_long_RL', 'pearsonr_long_RL', 'travel_long_RL', 'coverage_long_RL', 'jump_long_RL', 'longest_sequence_length_ratio_long_RL', 'direction_change_bin_ratio_long_RL', 'congruent_dir_bins_ratio_long_RL', 'total_congruent_direction_change_long_RL', 'P_Short_LR', 'score_short_LR', 'velocity_short_LR', 'intercept_short_LR', 'speed_short_LR', 'wcorr_short_LR', 'pearsonr_short_LR', 'travel_short_LR', 'coverage_short_LR', 'jump_short_LR', 'longest_sequence_length_ratio_short_LR', 'direction_change_bin_ratio_short_LR', 'congruent_dir_bins_ratio_short_LR', 'total_congruent_direction_change_short_LR', 'P_Short_RL', 'score_short_RL', 'velocity_short_RL', 'intercept_short_RL', 'speed_short_RL', 'wcorr_short_RL', 'pearsonr_short_RL', 'travel_short_RL', 'coverage_short_RL', 'jump_short_RL', 'longest_sequence_length_ratio_short_RL', 'direction_change_bin_ratio_short_RL', 'congruent_dir_bins_ratio_short_RL', 'total_congruent_direction_change_short_RL', 'ripple_start_t', 'long_best_travel', 'short_best_travel', 'travel_diff', 'long_best_coverage', 'short_best_coverage', 'coverage_diff', 'long_best_jump', 'short_best_jump', 'jump_diff', 'long_best_longest_sequence_length_ratio', 'short_best_longest_sequence_length_ratio', 'longest_sequence_length_ratio_diff', 'long_best_direction_change_bin_ratio', 'short_best_direction_change_bin_ratio', 'direction_change_bin_ratio_diff', 'long_best_congruent_dir_bins_ratio', 'short_best_congruent_dir_bins_ratio', 'congruent_dir_bins_ratio_diff', 'long_best_total_congruent_direction_change', 'short_best_total_congruent_direction_change', 'total_congruent_direction_change_diff', 'session_name', 'time_bin_size', 'delta_aligned_start_t']
# ['long_best_total_congruent_direction_change', 'short_best_total_congruent_direction_change']
['longest_sequence_length_ratio_diff', 'direction_change_bin_ratio_diff', 'congruent_dir_bins_ratio_diff', 'total_congruent_direction_change_diff']

In [ ]:
all_sessions_simple_pearson_ripple_df # 3138 rows × 24 columns

In [ ]:
all_sessions_simple_pearson_laps_df # 931 rows × 25 columns

In [ ]:
all_sessions_ripple_df # 17592 rows × 10 columns

In [ ]:
csv_files

In [ ]:
all_sessions_all_scores_ripple_df

In [ ]:

all_sessions_simple_pearson_ripple_df

In [ ]:
## find all columns starting with 'wcorr': wcorr_long_LR
sub_string: str = 'wcorr'
sub_string: str = 'pearsonr'
columns_list = list(all_sessions_simple_pearson_ripple_df.columns)
matching_columns = [s for s in columns_list if sub_string in s]
print(matching_columns) # ['wcorr_long_LR', 'wcorr_long_RL', 'wcorr_short_LR', 'wcorr_short_RL', 'long_best_wcorr', 'short_best_wcorr', 'wcorr_abs_diff']

['long_LR_pf_peak_x_pearsonr', 'long_RL_pf_peak_x_pearsonr', 'short_LR_pf_peak_x_pearsonr', 'short_RL_pf_peak_x_pearsonr', 'long_best_pf_peak_x_pearsonr', 'short_best_pf_peak_x_pearsonr', 'pearsonr_abs_diff']
['wcorr_long_LR', 'wcorr_long_RL', 'wcorr_short_LR', 'wcorr_short_RL', 'long_best_wcorr', 'short_best_wcorr', 'wcorr_abs_diff']

assert np.shape(all_sessions_simple_pearson_ripple_df)[0] == np.shape(all_sessions_all_scores_ripple_df)[0], f"np.shape(all_sessions_all_scores_ripple_df)[0]: {np.shape(all_sessions_all_scores_ripple_df)[0]} != np.shape(all_sessions_simple_pearson_ripple_df)[0]: {np.shape(all_sessions_simple_pearson_ripple_df)[0]}"



In [ ]:
['long_LR_pf_peak_x_pearsonr', 'long_RL_pf_peak_x_pearsonr', 'short_LR_pf_peak_x_pearsonr', 'short_RL_pf_peak_x_pearsonr', 'long_best_pf_peak_x_pearsonr', 'short_best_pf_peak_x_pearsonr', 'pearsonr_abs_diff']
['wcorr_long_LR', 'wcorr_long_RL', 'wcorr_short_LR', 'wcorr_short_RL', 'long_best_wcorr', 'short_best_wcorr', 'wcorr_abs_diff']

# 2024-03-02 - Get only the user-annotated ripples:

In [ ]:
from pyphoplacecellanalysis.SpecificResults.AcrossSessionResults import _split_user_annotated_ripple_df

## Bump
# input_df = all_sessions_simple_pearson_ripple_df
# input_df = all_sessions_all_scores_ripple_df

all_sessions_all_scores_ripple_df, (valid_ripple_df, invalid_ripple_df), (user_approved_ripple_df, user_rejected_ripple_df) = _split_user_annotated_ripple_df(all_sessions_all_scores_ripple_df)

## 2024-03-14 - 'is_valid_epoch' column
# 'is_valid_epoch'
## OUTPUTS: valid_ripple_df, invalid_ripple_df, user_approved_ripple_df, user_rejected_ripple_df, (user_annotated_epoch_unique_session_names, unannotated_session_names)
user_approved_ripple_df

### 2024-02-29 - 4pm - Filter the events for those meeting wcorr criteria:


In [ ]:
# df: pd.DataFrame = deepcopy(all_sessions_user_annotated_ripple_df)
df: pd.DataFrame = deepcopy(valid_ripple_df) # valid epochs, but not just those that the user approved
# df: pd.DataFrame = deepcopy(user_approved_ripple_df)

## INPUTS: df

min_wcorr_threshold: float = 0.33
min_wcorr_diff_threshold: float = 0.2

# is_included_large_wcorr_diff = np.any((df[['wcorr_abs_diff']].abs() > min_wcorr_diff_threshold), axis=1)
is_included_large_wcorr_diff = np.any((df[['wcorr_diff']].abs() > min_wcorr_diff_threshold), axis=1)
is_included_high_wcorr = np.any((df[['long_best_wcorr', 'short_best_wcorr']].abs() > min_wcorr_threshold), axis=1)

df = df[is_included_high_wcorr]
df

# wcorr_long_LR


In [ ]:
all_sessions_all_scores_ripple_df.time_bin_size.unique()

In [ ]:
all_sessions_ripple_time_bin_df

### Single-time bin size version:

In [ ]:
from pyphoplacecellanalysis.SpecificResults.PendingNotebookCode import build_single_time_bin_size_dfs


# target_time_bin_size: float = 0.005 # 0.025 # 0.08222222
target_time_bin_size: float = 0.025

## INPUTS: all_sessions_all_scores_ripple_df, (all_sessions_ripple_df, all_sessions_ripple_time_bin_df)
single_time_bin_size_all_sessions_ripple_df, single_time_bin_size_all_sessions_ripple_time_bin_df = build_single_time_bin_size_dfs(all_sessions_all_scores_epochs_df=all_sessions_all_scores_ripple_df,
                                                                                                            all_sessions_epochs_df=all_sessions_ripple_df, all_sessions_epochs_time_bin_df=all_sessions_ripple_time_bin_df, target_time_bin_size=0.005,
                                                                                                            included_columns = ['delta_aligned_start_t', 'is_user_annotated_epoch', 'is_valid_epoch'])

                                                                                                            
single_time_bin_size_all_sessions_laps_df, single_time_bin_size_all_sessions_laps_time_bin_df = build_single_time_bin_size_dfs(all_sessions_all_scores_epochs_df=all_sessions_simple_pearson_laps_df,
                                                                                                            all_sessions_epochs_df=all_sessions_laps_df, all_sessions_epochs_time_bin_df=all_sessions_laps_time_bin_df, target_time_bin_size=0.005,
                                                                                                            included_columns = ['delta_aligned_start_t',])

## OUTPUTS: single_time_bin_size_all_sessions_ripple_df, single_time_bin_size_all_sessions_ripple_time_bin_df
## OUTPUTS: single_time_bin_size_all_sessions_laps_df, single_time_bin_size_all_sessions_laps_time_bin_df 

single_time_bin_size_all_sessions_laps_df


# # Recover the important columns from the newer `all_sessions_all_scores_ripple_df`
# included_columns = ['delta_aligned_start_t', 'is_user_annotated_epoch', 'is_valid_epoch']  # Added 'delta_aligned_start_t' for the merge
# single_time_bin_size_all_sessions_ripple_df = pd.merge(single_time_bin_size_all_sessions_ripple_df, 
#                      all_sessions_all_scores_ripple_df[included_columns], 
#                      on='delta_aligned_start_t', 
#                      how='left')


# single_time_bin_size_all_sessions_ripple_df
## OUTPUTS: single_time_bin_size_all_sessions_ripple_df, single_time_bin_size_all_sessions_ripple_df
# single_time_bin_size_all_sessions_ripple_time_bin_df
all_sessions_simple_pearson_laps_df
single_time_bin_size_all_sessions_laps_time_bin_df

In [48]:
# INPUTS: all_sessions_all_scores_ripple_df, (all_sessions_ripple_df, all_sessions_ripple_time_bin_df)
all_sessions_ripple_df

P_LR      P_RL    P_Long   P_Short  ripple_idx  ripple_start_t  \
0      0.572743  0.427257  0.589042  0.410958           0       40.187177   
1      0.518085  0.481915  0.527867  0.472133           1       41.011916   
2      0.271274  0.728726  0.465855  0.534145           2       44.588736   
3      0.984812  0.015188  0.841381  0.158619           3       45.379714   
4      0.455694  0.544306  0.804823  0.195177           4       45.994329   
...         ...       ...       ...       ...         ...             ...   
44194  0.514383  0.485617  0.396319  0.603681          90     1429.924337   
44195  0.409463  0.590537  0.331976  0.668024          91     1435.942904   
44196  0.643907  0.356093  0.512303  0.487697          92     1437.783184   
44197  0.652461  0.347539  0.641944  0.358056          93     1445.197729   
44198  0.715728  0.284272  0.473291  0.526709          94     1456.458569   

                             session_name  delta_aligned_start_t  \
0      kdiba_gor01_one_2006-6-08_14-26-15           -1171.370903   
1      kdiba_gor01_one_2006-6-08_14-26-15           -1170.546164   
2      kdiba_gor01_one_2006-6-08_14-26-15           -1166.969344   
3      kdiba_gor01_one_2006-6-08_14-26-15           -1166.178366   
4      kdiba_gor01_one_2006-6-08_14-26-15           -1165.563751   
...                                   ...                    ...   
44194   kdiba_vvp01_two_2006-4-10_12-58-3             497.098131   
44195   kdiba_vvp01_two_2006-4-10_12-58-3             503.116698   
44196   kdiba_vvp01_two_2006-4-10_12-58-3             504.956978   
44197   kdiba_vvp01_two_2006-4-10_12-58-3             512.371523   
44198   kdiba_vvp01_two_2006-4-10_12-58-3             523.632363   

       time_bin_size                                 custom_replay_name  \
0                NaN                                                      
1                NaN                                                      
2                NaN                                                      
3                NaN                                                      
4                NaN                                                      
...              ...                                                ...   
44194            NaN  withNormalComputedReplays-qclu_[1,2]-frateThre...   
44195            NaN  withNormalComputedReplays-qclu_[1,2]-frateThre...   
44196            NaN  withNormalComputedReplays-qclu_[1,2]-frateThre...   
44197            NaN  withNormalComputedReplays-qclu_[1,2]-frateThre...   
44198            NaN  withNormalComputedReplays-qclu_[1,2]-frateThre...   

       epoch_idx  is_valid_epoch  is_user_annotated_epoch  \
0              0            True                    False   
1              1            True                    False   
2              2            True                    False   
3              3            True                    False   
4              4            True                    False   
...          ...             ...                      ...   
44194         90            True                    False   
44195         91            True                    False   
44196         92            True                    False   
44197         93            True                    False   
44198         94            True                    False   

      pre_post_delta_category  
0                   pre-delta  
1                   pre-delta  
2                   pre-delta  
3                   pre-delta  
4                   pre-delta  
...                       ...  
44194              post-delta  
44195              post-delta  
44196              post-delta  
44197              post-delta  
44198              post-delta  

[44199 rows x 14 columns]

In [49]:
all_sessions_ripple_time_bin_df

P_LR          P_RL    P_Long   P_Short  epoch_idx  t_bin_center  \
0       0.026580  9.734196e-01  0.589377  0.410623          0     40.202177   
1       0.096444  9.035562e-01  0.794633  0.205367          0     40.232177   
2       0.813426  1.865735e-01  0.420990  0.579010          0     40.262177   
3       1.000000  1.617739e-07  0.996191  0.003809          0     40.292177   
4       0.616201  3.837986e-01  0.867583  0.132417          0     40.322177   
...          ...           ...       ...       ...        ...           ...   
404173  0.835499  1.645006e-01  0.527145  0.472855         94   1456.788569   
404174  0.510939  4.890609e-01  0.432948  0.567052         94   1456.808569   
404175  0.742843  2.571566e-01  0.288136  0.711864         94   1456.828569   
404176  0.510939  4.890609e-01  0.432948  0.567052         94   1456.848569   
404177  0.952987  4.701313e-02  0.467316  0.532684         94   1456.868569   

                              session_name  delta_aligned_start_t  \
0       kdiba_gor01_one_2006-6-08_14-26-15           -1171.355903   
1       kdiba_gor01_one_2006-6-08_14-26-15           -1171.325903   
2       kdiba_gor01_one_2006-6-08_14-26-15           -1171.295903   
3       kdiba_gor01_one_2006-6-08_14-26-15           -1171.265903   
4       kdiba_gor01_one_2006-6-08_14-26-15           -1171.235903   
...                                    ...                    ...   
404173   kdiba_vvp01_two_2006-4-10_12-58-3             523.962363   
404174   kdiba_vvp01_two_2006-4-10_12-58-3             523.982363   
404175   kdiba_vvp01_two_2006-4-10_12-58-3             524.002363   
404176   kdiba_vvp01_two_2006-4-10_12-58-3             524.022363   
404177   kdiba_vvp01_two_2006-4-10_12-58-3             524.042363   

        time_bin_size                                 custom_replay_name  \
0                 NaN                                                      
1                 NaN                                                      
2                 NaN                                                      
3                 NaN                                                      
4                 NaN                                                      
...               ...                                                ...   
404173            NaN  withNormalComputedReplays-qclu_[1,2]-frateThre...   
404174            NaN  withNormalComputedReplays-qclu_[1,2]-frateThre...   
404175            NaN  withNormalComputedReplays-qclu_[1,2]-frateThre...   
404176            NaN  withNormalComputedReplays-qclu_[1,2]-frateThre...   
404177            NaN  withNormalComputedReplays-qclu_[1,2]-frateThre...   

       pre_post_delta_category  
0                    pre-delta  
1                    pre-delta  
2                    pre-delta  
3                    pre-delta  
4                    pre-delta  
...                        ...  
404173              post-delta  
404174              post-delta  
404175              post-delta  
404176              post-delta  
404177              post-delta  

[404178 rows x 11 columns]

# Plotting via Plotly
`!pip install kaleido=="v0.1.0.post1" `

In [73]:
import plotly.io as pio
from pyphoplacecellanalysis.Pho2D.plotly.plotly_templates import PlotlyHelpers
from pyphoplacecellanalysis.Pho2D.statistics_plotting_helpers import plot_histograms_across_sessions, plot_stacked_histograms
from pyphoplacecellanalysis.Pho2D.plotly.Extensions.plotly_helpers import plotly_helper_save_figures, _helper_build_figure, plotly_pre_post_delta_scatter, plot_across_sessions_scatter_results

# fig_size_kwargs = {'width': 1650, 'height': 480}
resolution_multiplier = 1
fig_size_kwargs = {'width': resolution_multiplier*1650, 'height': resolution_multiplier*480}
is_dark_mode, template = PlotlyHelpers.get_plotly_template(is_dark_mode=False)
pio.templates.default = template

# figure_export_path = Path(r'E:\Dropbox (Personal)\Active\Kamran Diba Lab\Presentations\2024-05-30 - Pho iNAV Poster\Figures').resolve()
# figure_export_path = Path('/Users/pho/Dropbox (Personal)/Active/Kamran Diba Lab/Presentations/2024-05-30 - Pho iNAV Poster/Figures').resolve()

# assert figure_export_path.exists()

from PIL import Image

from pyphocorehelpers.programming_helpers import copy_image_to_clipboard

def save_plotly(a_fig, a_fig_context):
    """ 
    captures: TODAY_DAY_DATE, figures_folder, neptuner_run
    """
    fig_save_path: Path = figures_folder.joinpath('_'.join([TODAY_DAY_DATE, sanitize_filename_for_Windows(a_fig_context.get_description())])).resolve()
    figure_out_paths = {'.html': fig_save_path.with_suffix('.html'), '.png': fig_save_path.with_suffix('.png')}
    a_fig.write_html(figure_out_paths['.html'])
    display(fullwidth_path_widget(figure_out_paths['.html'], file_name_label='.html'))
    # print(file_uri_from_path(figure_out_paths['.html']))
    a_fig.write_image(figure_out_paths['.png'])
    # print(file_uri_from_path(figure_out_paths['.png']))
    display(fullwidth_path_widget(figure_out_paths['.png'], file_name_label='.png'))

    if neptuner_run is not None:
        a_full_figure_path_key: str = a_fig_context.get_description(separator='/', include_property_names=True, key_value_separator=':') # .replace(' ', '_')
        # a_full_figure_path_key: str = a_fig_context.get_description(separator=':', include_property_names=True, key_value_separator='|')
        print(f'a_full_figure_path_key: "{a_full_figure_path_key}"')
        # neptuner_run['outputs']['figures'][f"{a_full_figure_path_key}"].upload(a_fig)
        neptuner_run['outputs']['figures'][f"{a_full_figure_path_key}"].upload(figure_out_paths['.html'].as_posix())
        # neptuner.figures[f"{a_full_figure_path_key}"].upload(a_fig)
        
    return figure_out_paths


In [78]:
histogram_bins = 25
num_sessions = 1


# concatenated_ripple_df = deepcopy(df)
## INPUTS: all_sessions_all_scores_ripple_df

# concatenated_ripple_df = deepcopy(concatenated_ripple_df)
# concatenated_ripple_df = deepcopy(all_sessions_ripple_df)

concatenated_ripple_df = deepcopy(filtered_all_sessions_wcorr_ripple_df)

# concatenated_ripple_df = deepcopy(all_sessions_ripple_time_bin_df)
# concatenated_ripple_df = deepcopy(all_sessions_all_scores_ripple_df)
# concatenated_ripple_df = deepcopy(single_time_bin_size_all_sessions_ripple_df)
concatenated_ripple_df
# ['longest_sequence_length_ratio_diff', 'direction_change_bin_ratio_diff', 'congruent_dir_bins_ratio_diff', 'total_congruent_direction_change_diff']


# variable_name = 'P_Long'
variable_name = 'P_Short' # Shows expected effect - short-only replay prior to delta and then split replays post-delta
# variable_name = 'long_best_pf_peak_x_pearsonr'
# variable_name = 'long_best_jump'
# variable_name = 'wcorr_abs_diff'
# variable_name = 'pearsonr_abs_diff'
# variable_name = 'direction_change_bin_ratio_diff'
# variable_name = 'longest_sequence_length_ratio_diff'
# variable_name = 'long_best_longest_sequence_length_ratio'
# variable_name = 'long_best_congruent_dir_bins_ratio'
# variable_name = 'congruent_dir_bins_ratio_diff'
# variable_name = 'total_congruent_direction_change_diff'
# variable_name = 'long_best_congruent_dir_bins_ratio'
# variable_name = 'long_best_direction_change_bin_ratio'
# variable_name = 'long_best_congruent_dir_bins_ratio'
# 'color':'is_user_annotated_epoch'
# 'color': 'is_user_annotated_epoch', 

# px_scatter_kwargs = {'x': 'delta_aligned_start_t', 'y': variable_name, 'color':"is_user_annotated_epoch", 'title': f"'{variable_name}'"} # , 'color': 'time_bin_size', 'range_y': [-1.0, 1.0], 'labels': {'session_name': 'Session', 'time_bin_size': 'tbin_size', 'is_user_annotated_epoch':'user_sel'}
px_scatter_kwargs = {'x': 'delta_aligned_start_t', 'y': variable_name, 'title': f"'{variable_name}'"} # , 'color': 'time_bin_size', 'range_y': [-1.0, 1.0], 'labels': {'session_name': 'Session', 'time_bin_size': 'tbin_size', 'is_user_annotated_epoch':'user_sel'}
# px_scatter_kwargs.pop('color')

# hist_kwargs = dict(color="time_bin_size")
hist_kwargs = dict(color="is_user_annotated_epoch") # , histnorm='probability density'
hist_kwargs.pop('color')
# new_fig_ripples, new_fig_ripples_context = plotly_pre_post_delta_scatter(data_results_df=concatenated_ripple_df, out_scatter_fig=None, histogram_bins=histogram_bins,
#                         px_scatter_kwargs=px_scatter_kwargs, histogram_variable_name=variable_name, hist_kwargs=hist_kwargs, forced_range_y=None,
#                         time_delta_tuple=(earliest_delta_aligned_t_start, 0.0, latest_delta_aligned_t_end), legend_title_text='Is User Selected', is_dark_mode=is_dark_mode)

new_fig_ripples, new_fig_ripples_context = plotly_pre_post_delta_scatter(data_results_df=concatenated_ripple_df, out_scatter_fig=None, histogram_bins=histogram_bins,
                        px_scatter_kwargs=px_scatter_kwargs, histogram_variable_name=variable_name, hist_kwargs=hist_kwargs, forced_range_y=None,
                        time_delta_tuple=(earliest_delta_aligned_t_start, 0.0, latest_delta_aligned_t_end), legend_title_text=None, is_dark_mode=is_dark_mode)

new_fig_ripples = new_fig_ripples.update_layout(fig_size_kwargs)

_extras_output_dict = {}
_extras_output_dict["y_mid_line"] = new_fig_ripples.add_hline(y=0.5, line=dict(color="rgba(0.8,0.8,0.8,.75)", width=2), row='all', col='all')

# # Update layout to add a title to the legend
# new_fig_ripples.update_layout(
#     legend_title_text='Is User Selected'  # Add a title to the legend
# )

# fig_to_clipboard(new_fig_ripples, **fig_size_kwargs)
new_fig_ripples_context = new_fig_ripples_context.adding_context_if_missing(num_sessions=num_sessions, plot_type='scatter+hist', comparison='pre-post-delta', variable_name=variable_name)
figure_out_paths = save_plotly(a_fig=new_fig_ripples, a_fig_context=new_fig_ripples_context)
new_fig_ripples

num_unique_sessions: 7, num_unique_time_bins: 1
num_unique_sessions: 7, num_unique_time_bins: 1
num_unique_sessions: 7, num_unique_time_bins: 1
len(pre_delta_fig.data): 1


Box(children=(Label(value='.html', layout=Layout(width='auto')), HTML(value="<b style='font-size: larger;'>K:\…

Box(children=(Label(value='.png', layout=Layout(width='auto')), HTML(value="<b style='font-size: larger;'>K:\\…

In [81]:
histogram_bins = 25
num_sessions = 1

concatenated_ripple_df = deepcopy(filtered_all_sessions_wcorr_ripple_df)


# variable_name = 'P_Long'
variable_name = 'P_Short' # Shows expected effect - short-only replay prior to delta and then split replays post-delta
# variable_name = 'long_best_pf_peak_x_pearsonr'
# variable_name = 'long_best_jump'
# variable_name = 'wcorr_abs_diff'
# variable_name = 'pearsonr_abs_diff'
# variable_name = 'direction_change_bin_ratio_diff'
# variable_name = 'longest_sequence_length_ratio_diff'
# variable_name = 'long_best_longest_sequence_length_ratio'
# variable_name = 'long_best_congruent_dir_bins_ratio'
# variable_name = 'congruent_dir_bins_ratio_diff'
# variable_name = 'total_congruent_direction_change_diff'
# variable_name = 'long_best_congruent_dir_bins_ratio'
# variable_name = 'long_best_direction_change_bin_ratio'
# variable_name = 'long_best_congruent_dir_bins_ratio'
# 'color':'is_user_annotated_epoch'
# 'color': 'is_user_annotated_epoch', 

# px_scatter_kwargs = {'x': 'delta_aligned_start_t', 'y': variable_name, 'color':"is_user_annotated_epoch", 'title': f"'{variable_name}'"} # , 'color': 'time_bin_size', 'range_y': [-1.0, 1.0], 'labels': {'session_name': 'Session', 'time_bin_size': 'tbin_size', 'is_user_annotated_epoch':'user_sel'}
px_scatter_kwargs = {'x': 'delta_aligned_start_t', 'y': variable_name, 'title': f"'{variable_name}'"} # , 'color': 'time_bin_size', 'range_y': [-1.0, 1.0], 'labels': {'session_name': 'Session', 'time_bin_size': 'tbin_size', 'is_user_annotated_epoch':'user_sel'}
# px_scatter_kwargs.pop('color')

# hist_kwargs = dict(color="time_bin_size")
hist_kwargs = dict(color="is_user_annotated_epoch") # , histnorm='probability density'
hist_kwargs.pop('color')
# new_fig_ripples, new_fig_ripples_context = plotly_pre_post_delta_scatter(data_results_df=concatenated_ripple_df, out_scatter_fig=None, histogram_bins=histogram_bins,
#                         px_scatter_kwargs=px_scatter_kwargs, histogram_variable_name=variable_name, hist_kwargs=hist_kwargs, forced_range_y=None,
#                         time_delta_tuple=(earliest_delta_aligned_t_start, 0.0, latest_delta_aligned_t_end), legend_title_text='Is User Selected', is_dark_mode=is_dark_mode)

new_fig_ripples, new_fig_ripples_context = plotly_pre_post_delta_scatter(data_results_df=concatenated_ripple_df, out_scatter_fig=None, histogram_bins=histogram_bins,
                        px_scatter_kwargs=px_scatter_kwargs, histogram_variable_name=variable_name, hist_kwargs=hist_kwargs, forced_range_y=None,
                        time_delta_tuple=(earliest_delta_aligned_t_start, 0.0, latest_delta_aligned_t_end), legend_title_text=None, is_dark_mode=is_dark_mode)

new_fig_ripples = new_fig_ripples.update_layout(fig_size_kwargs)

_extras_output_dict = {}
_extras_output_dict["y_mid_line"] = new_fig_ripples.add_hline(y=0.5, line=dict(color="rgba(0.8,0.8,0.8,.75)", width=2), row='all', col='all')

# # Update layout to add a title to the legend
# new_fig_ripples.update_layout(
#     legend_title_text='Is User Selected'  # Add a title to the legend
# )

# fig_to_clipboard(new_fig_ripples, **fig_size_kwargs)
new_fig_ripples_context = new_fig_ripples_context.adding_context_if_missing(num_sessions=num_sessions, plot_type='scatter+hist', comparison='pre-post-delta', variable_name=variable_name)
figure_out_paths = save_plotly(a_fig=new_fig_ripples, a_fig_context=new_fig_ripples_context)
new_fig_ripples

num_unique_sessions: 7, num_unique_time_bins: 1
num_unique_sessions: 7, num_unique_time_bins: 1
num_unique_sessions: 7, num_unique_time_bins: 1
len(pre_delta_fig.data): 1


Box(children=(Label(value='.html', layout=Layout(width='auto')), HTML(value="<b style='font-size: larger;'>K:\…

Box(children=(Label(value='.png', layout=Layout(width='auto')), HTML(value="<b style='font-size: larger;'>K:\\…

In [79]:
# variable_name = 'short_best_direction_change_bin_ratio'
# variable_name = 'long_best_congruent_dir_bins_ratio'
variable_name = 'short_best_wcorr'
# 'color':'is_user_annotated_epoch'
# 'color': 'is_user_annotated_epoch', 
px_scatter_kwargs = {'x': 'delta_aligned_start_t', 'y': variable_name, 'color':"pre_post_delta_category", 'title': f"'{variable_name}'"} # , 'color': 'time_bin_size', 'range_y': [-1.0, 1.0], , 'labels': {'session_name': 'Session', 'time_bin_size': 'tbin_size', 'is_user_annotated_epoch':'user_sel'}
# hist_kwargs = dict(color="time_bin_size")
hist_kwargs = dict(color="pre_post_delta_category") # , histnorm='probability density'
new_fig_ripples, figure_context = plotly_pre_post_delta_scatter(data_results_df=concatenated_ripple_df, out_scatter_fig=None, histogram_bins=histogram_bins,
                        px_scatter_kwargs=px_scatter_kwargs, histogram_variable_name=variable_name, hist_kwargs=hist_kwargs, forced_range_y=None,
                        time_delta_tuple=(earliest_delta_aligned_t_start, 0.0, latest_delta_aligned_t_end), is_dark_mode=is_dark_mode)
_extras_output_dict = {}
_extras_output_dict["y_mid_line"] = new_fig_ripples.add_hline(y=0.0, line=dict(color="rgba(0.8,0.8,0.8,.75)", width=2), row='all', col='all')
new_fig_ripples.update_layout(fig_size_kwargs)
new_fig_ripples.show()
figure_out_paths = save_plotly(a_fig=new_fig_ripples, a_fig_context=figure_context)


num_unique_sessions: 7, num_unique_time_bins: 1
num_unique_sessions: 7, num_unique_time_bins: 1
num_unique_sessions: 7, num_unique_time_bins: 1


ValueError: Value of 'y' is not the name of a column in 'data_frame'. Expected one of ['P_LR', 'P_RL', 'P_Long', 'P_Short', 'ripple_idx', 'ripple_start_t', 'P_Long_LR', 'P_Long_RL', 'P_Short_LR', 'P_Short_RL', 'most_likely_decoder_index', 'wcorr_long_LR', 'wcorr_long_RL', 'wcorr_short_LR', 'wcorr_short_RL', 'best_decoder_index', 'session_name', 'time_bin_size', 'delta_aligned_start_t', 'is_user_annotated_epoch', 'is_valid_epoch', 'custom_replay_name', 'epoch_idx'] but received: short_best_wcorr

In [37]:
# variable_name = 'total_congruent_direction_change_diff'
# variable_name = 'long_best_congruent_dir_bins_ratio'
# variable_name = 'long_best_total_congruent_direction_change'
variable_name = 'wcorr_diff'
# variable_name = 'long_best_wcorr'
# 'color':'is_user_annotated_epoch'
# 'color': 'is_user_annotated_epoch', 
px_scatter_kwargs = {'x': 'delta_aligned_start_t', 'y': variable_name, 'color':"is_user_annotated_epoch", 'title': f"'{variable_name}'", 'labels': {'session_name': 'Session', 'time_bin_size': 'tbin_size', 'is_user_annotated_epoch':'user_sel'}} # , 'color': 'time_bin_size', 'range_y': [-1.0, 1.0], 
# hist_kwargs = dict(color="time_bin_size")
hist_kwargs = dict(color="is_user_annotated_epoch") # , histnorm='probability density'
new_fig_ripples, figure_context = plotly_pre_post_delta_scatter(data_results_df=concatenated_ripple_df, out_scatter_fig=None, histogram_bins=histogram_bins,
                        px_scatter_kwargs=px_scatter_kwargs, histogram_variable_name=variable_name, hist_kwargs=hist_kwargs, forced_range_y=None,
                        time_delta_tuple=(earliest_delta_aligned_t_start, 0.0, latest_delta_aligned_t_end), is_dark_mode=is_dark_mode)
_extras_output_dict = {}
_extras_output_dict["y_mid_line"] = new_fig_ripples.add_hline(y=0.0, line=dict(color="rgba(0.8,0.8,0.8,.75)", width=2), row='all', col='all')
new_fig_ripples.update_layout(fig_size_kwargs)
new_fig_ripples.show()

figure_context = figure_context.adding_context_if_missing(num_sessions=num_sessions, plot_type='scatter+hist', comparison='pre-post-delta', variable_name=variable_name)
figure_out_paths = save_plotly(a_fig=new_fig_ripples, a_fig_context=figure_context)


num_unique_sessions: 8, num_unique_time_bins: 1
num_unique_sessions: 8, num_unique_time_bins: 1
num_unique_sessions: 8, num_unique_time_bins: 1
len(pre_delta_fig.data): 2


Box(children=(Label(value='.html', layout=Layout(width='auto')), HTML(value="<b style='font-size: larger;'>K:\…

Box(children=(Label(value='.png', layout=Layout(width='auto')), HTML(value="<b style='font-size: larger;'>K:\\…

## Stats Tests

In [38]:
from pyphoplacecellanalysis.SpecificResults.PendingNotebookCode import _perform_stats_tests


# stats_variable_name: str = 'P_Short'
# stats_variable_name: str = 'short_best_direction_change_bin_ratio'
# stats_variable_name: str = 'short_best_wcorr'
shuffle_results, p_value, f_value, (dof1, dof2), (variance1, variance2) = _perform_stats_tests(valid_ripple_df, stats_variable_name='short_best_wcorr')


ImportError: cannot import name '_perform_stats_tests' from 'pyphoplacecellanalysis.SpecificResults.PendingNotebookCode' (C:\Users\pho\repos\Spike3DWorkEnv\pyPhoPlaceCellAnalysis\src\pyphoplacecellanalysis\SpecificResults\PendingNotebookCode.py)

In [ ]:
# Show that wcorr in both periods is higher than shuffles


In [39]:
## User non-selected:
scatter_title = f'user_approved_ripple_df Several Sessions {variable_name}'
# variable_name = 'wcorr_abs_diff'
px_scatter_kwargs = {'x': 'delta_aligned_start_t', 'y': variable_name, 'title': scatter_title, 'range_y': [0.0, 1.0], 'labels': {'session_name': 'Session', 'time_bin_size': 'tbin_size'}} # , 'color': 'time_bin_size'
new_fig_ripples, figure_context = plotly_pre_post_delta_scatter(data_results_df=deepcopy(user_approved_ripple_df), out_scatter_fig=None, histogram_bins=histogram_bins,
                        px_scatter_kwargs=px_scatter_kwargs, histogram_variable_name=variable_name, forced_range_y=None,
                        time_delta_tuple=(earliest_delta_aligned_t_start, 0.0, latest_delta_aligned_t_end), is_dark_mode=is_dark_mode)
_extras_output_dict["y_mid_line"] = new_fig_ripples.add_hline(y=0.5, line=dict(color="rgba(0.8,0.8,0.8,.75)", width=2), row='all', col='all')
new_fig_ripples.update_layout(fig_size_kwargs)
new_fig_ripples

num_unique_sessions: 8, num_unique_time_bins: 1
num_unique_sessions: 8, num_unique_time_bins: 1
num_unique_sessions: 8, num_unique_time_bins: 1
len(pre_delta_fig.data): 1


In [ ]:
# IDEA: The ones with clear replays (diagonal sequences in the decoded posteriors) are by definiition ambiguous, because there's not much difference between the long/short decoders.


In [40]:
## User non-selected:
scatter_title = f'Non-selected Several Sessions {variable_name}'
# variable_name = 'wcorr_abs_diff'
px_scatter_kwargs = {'x': 'delta_aligned_start_t', 'y': variable_name, 'title': scatter_title, 'range_y': [0.0, 1.0], 'labels': {'session_name': 'Session', 'time_bin_size': 'tbin_size'}} # , 'color': 'time_bin_size'
new_fig_ripples, figure_context = plotly_pre_post_delta_scatter(data_results_df=deepcopy(user_rejected_ripple_df), out_scatter_fig=None, histogram_bins=histogram_bins,
                        px_scatter_kwargs=px_scatter_kwargs, histogram_variable_name=variable_name, forced_range_y=None,
                        time_delta_tuple=(earliest_delta_aligned_t_start, 0.0, latest_delta_aligned_t_end))
new_fig_ripples.update_layout(fig_size_kwargs)
new_fig_ripples


num_unique_sessions: 8, num_unique_time_bins: 1
num_unique_sessions: 8, num_unique_time_bins: 1
num_unique_sessions: 8, num_unique_time_bins: 1
len(pre_delta_fig.data): 1


In [41]:
# Laps test
concatenated_ripple_df = deepcopy(all_sessions_simple_pearson_laps_df)

scatter_title = 'Several Sessions'
variable_name = 'wcorr_abs_diff'
px_scatter_kwargs = {'x': 'delta_aligned_start_t', 'y': variable_name, 'title': scatter_title, 'range_y': [0.0, 1.0], 'labels': {'session_name': 'Session', 'time_bin_size': 'tbin_size'}} 
new_fig_ripples, figure_context = plotly_pre_post_delta_scatter(data_results_df=deepcopy(concatenated_ripple_df), out_scatter_fig=None, histogram_bins=histogram_bins,
                        px_scatter_kwargs=px_scatter_kwargs, histogram_variable_name=variable_name, forced_range_y=None,
                        time_delta_tuple=(earliest_delta_aligned_t_start, 0.0, latest_delta_aligned_t_end))
new_fig_ripples.update_layout(fig_size_kwargs)
new_fig_ripples


num_unique_sessions: 14, num_unique_time_bins: 9
num_unique_sessions: 14, num_unique_time_bins: 9
num_unique_sessions: 14, num_unique_time_bins: 9
len(pre_delta_fig.data): 1


# Plotting functions

In [42]:
from pyphoplacecellanalysis.General.Model.Configs.LongShortDisplayConfig import PlottingHelpers
# from pyphoplacecellanalysis.SpecificResults.AcrossSessionResults import plot_across_sessions_scatter_results

# Example usage:
all_session_figures = plot_across_sessions_scatter_results(collected_outputs_directory, concatenated_laps_df=all_sessions_laps_df, concatenated_ripple_df=all_sessions_ripple_df,
														#    enabled_time_bin_sizes=[0.03, 0.10],
														   earliest_delta_aligned_t_start=earliest_delta_aligned_t_start, latest_delta_aligned_t_end=latest_delta_aligned_t_end,
														   laps_title_prefix=f"Laps", ripple_title_prefix=f"Ripples", save_figures=True, figure_save_extension=['.html','.png'], is_dark_mode=is_dark_mode)
fig_laps, fig_ripples = all_session_figures[0]
# fig_laps.update_layout(fig_size_kwargs)
# fig_ripples.update_layout(fig_size_kwargs)

# fig_laps.show()
fig_ripples.show()
# fig_laps.write_html(f"../output/{TODAY_DAY_DATE}_AcrossSession_fig_laps.html")
# fig_ripples.write_html(f"../output/{TODAY_DAY_DATE}_AcrossSession_fig_ripples.html")


plot_across_sessions_results(directory: K:\scratch\collected_outputs)
	figures_folder: file:///K:/scratch/collected_outputs/figures
num_unique_sessions: 16, num_unique_time_bins: 2
main_plot_mode: separate_row_per_session
num_unique_sessions: 16, num_unique_time_bins: 2
main_plot_mode: separate_row_per_session
	saving figures...
	saving "file:///K:/scratch/collected_outputs/figures/16-Sessions_laps_marginal.html"...
	saving "file:///K:/scratch/collected_outputs/figures/16-Sessions_ripples_marginal.html"...
	saving "file:///K:/scratch/collected_outputs/figures/16-Sessions_laps_marginal.png"...
	saving "file:///K:/scratch/collected_outputs/figures/16-Sessions_ripples_marginal.png"...


In [ ]:
figure_context = figure_context.adding_context_if_missing(num_sessions=num_sessions, plot_type='scatter+hist', comparison='pre-post-delta', variable_name=variable_name)



In [ ]:
fig_to_clipboard(fig_ripples)

In [ ]:
## time_bin version:
all_time_bin_session_figures = plot_across_sessions_scatter_results(collected_outputs_directory, concatenated_laps_df=all_sessions_laps_time_bin_df, concatenated_ripple_df=all_sessions_ripple_time_bin_df,
														#    enabled_time_bin_sizes=[0.03, 0.10],
														   earliest_delta_aligned_t_start=earliest_delta_aligned_t_start, latest_delta_aligned_t_end=latest_delta_aligned_t_end,
														   main_plot_mode='separate_row_per_session',
														   laps_title_prefix=f"Laps_per_time_bin", ripple_title_prefix=f"Ripples_per_time_bin", save_figures=True, figure_save_extension=['.html','.png'], is_dark_mode=is_dark_mode)
fig_time_bin_laps, fig_time_bin_ripples = all_time_bin_session_figures[0]
# fig_time_bin_laps.show()
fig_time_bin_ripples.show()

In [ ]:
## Test collapsed histograms-only results:
histograms_only_all_time_bin_session_figures = plot_across_sessions_scatter_results(collected_outputs_directory, concatenated_laps_df=all_sessions_laps_time_bin_df, concatenated_ripple_df=all_sessions_ripple_time_bin_df,
														#    enabled_time_bin_sizes=[0.03, 0.10],
															# enabled_time_bin_sizes=[0.03, 0.058, 0.10], # [0.03 , 0.044, 0.058, 0.072, 0.086, 0.1]
														   earliest_delta_aligned_t_start=earliest_delta_aligned_t_start, latest_delta_aligned_t_end=latest_delta_aligned_t_end,
														   main_plot_mode='default',
														   laps_title_prefix=f"Laps_per_time_bin", ripple_title_prefix=f"Ripples_per_time_bin", save_figures=False, figure_save_extension=['.html','.png'])
histograms_only_fig_time_bin_laps, histograms_only_fig_time_bin_ripples = histograms_only_all_time_bin_session_figures[0]
# histograms_only_fig_time_bin_laps.show()
histograms_only_fig_time_bin_ripples.show()

In [ ]:
import plotly.subplots as sp
import plotly.graph_objs as go


all_session_figures = plot_across_sessions_scatter_results(collected_outputs_directory, concatenated_laps_df=single_time_bin_size_all_sessions_laps_df, concatenated_ripple_df=single_time_bin_size_all_sessions_ripple_df,
														#    enabled_time_bin_sizes=[0.03, 0.10],
														   earliest_delta_aligned_t_start=earliest_delta_aligned_t_start, latest_delta_aligned_t_end=latest_delta_aligned_t_end,
														   laps_title_prefix=f"Laps", ripple_title_prefix=f"Ripples", save_figures=True, figure_save_extension=['.html','.png'], is_dark_mode=is_dark_mode, main_plot_mode='default')
fig_laps, fig_ripples = all_session_figures[0]


In [ ]:
from pyphoplacecellanalysis.Pho2D.plotly.Extensions.plotly_helpers import plotly_pre_post_delta_scatter

# data_results_df: pd.DataFrame = deepcopy(all_sessions_laps_df) # all_sessions_laps_time_bin_df
data_results_df: pd.DataFrame = deepcopy(single_time_bin_size_all_sessions_laps_time_bin_df).infer_objects()

# histogram_bins = 'auto'
histogram_bins: int = 25
new_laps_fig, new_laps_fig_context = plotly_pre_post_delta_scatter(data_results_df=data_results_df, out_scatter_fig=fig_laps, histogram_bins=histogram_bins, px_scatter_kwargs=dict(title='Laps'))


# new_laps_fig = new_laps_fig.update_layout(fig_size_kwargs, 
#     xaxis_title="X Axis Title",
#     yaxis_title="Y Axis Title",
#     legend_title="Legend Title",
#     font=dict(
#         family="Courier New, monospace",
#         size=18,
#         color="RebeccaPurple"
#     ),
# )
# Update x-axis labels
# new_laps_fig.update_xaxes(title_text="Num Time Bins", row=1, col=1)
# new_laps_fig.update_xaxes(title_text="Delta-aligned Event Time (seconds)", row=1, col=2)
# new_laps_fig.update_xaxes(title_text="Num Time Bins", row=1, col=3)


_extras_output_dict = {}
_extras_output_dict["y_mid_line"] = new_laps_fig.add_hline(y=0.5, line=dict(color="rgba(0.8,0.8,0.8,.75)", width=2), row='all', col='all')

new_laps_fig

# # Update layout to add a title to the legend
# new_fig_ripples.update_layout(
#     legend_title_text='Is User Selected'  # Add a title to the legend
# )

# fig_to_clipboard(new_fig_ripples, **fig_size_kwargs)

new_laps_fig_context: IdentifyingContext = new_laps_fig_context.adding_context_if_missing(epoch='laps', num_sessions=num_sessions, plot_type='scatter+hist', comparison='pre-post-delta', variable_name=variable_name)
figure_out_paths = save_plotly(a_fig=new_laps_fig, a_fig_context=new_laps_fig_context)
new_laps_fig

In [ ]:
data_results_df


In [ ]:
np.unique(data_results_df['time_bin_size'])


In [ ]:

data_results_df[data_results_df['time_bin_size'] == 0.005]

# Matplotlib-based versions:

In [ ]:
from pyphoplacecellanalysis.Pho2D.statistics_plotting_helpers import plot_histograms_across_sessions, plot_stacked_histograms

matplotlib.use('Qt5Agg')


In [ ]:

# #TODO 2024-06-05 09:15: - [ ] Define save_matplotlib function
new_laps_fig_context: IdentifyingContext = new_laps_fig_context.adding_context_if_missing(epoch='laps', num_sessions=num_sessions, plot_type='scatter+hist', comparison='pre-post-delta', variable_name=variable_name)

In [ ]:
# from Spike3D.PendingNotebookCode import plot_stacked_histograms

# You can use it like this:'long_best_dir_simple_pearsonr'
_out0: "MatplotlibRenderPlots" = plot_histograms_across_sessions(data_type='Laps', session_spec='All Sessions', data_results_df=all_sessions_laps_time_bin_df, time_bin_duration_str="75 ms")
_out1: "MatplotlibRenderPlots" = plot_histograms_across_sessions(data_type='Ripples', session_spec='All Sessions', data_results_df=all_sessions_ripple_time_bin_df, time_bin_duration_str="75 ms")

In [ ]:


fig_to_clipboard(_out0.figures[0])

In [ ]:
## all_sessions_new_laps_df, all_sessions_new_ripple_df
_out0: "MatplotlibRenderPlots" = plot_histograms_across_sessions(data_type='New Laps', session_spec='All Sessions', data_results_df=all_sessions_new_laps_df, time_bin_duration_str="25 ms")
_out1: "MatplotlibRenderPlots" = plot_histograms_across_sessions(data_type='New Ripples', session_spec='All Sessions', data_results_df=all_sessions_new_ripple_df, time_bin_duration_str="25 ms")



In [ ]:
all_sessions_new_laps_df

In [ ]:
len(all_sessions_new_laps_df['session_name'].unique()) # 10 sessions



In [ ]:

matplotlib.use('Qt5Agg')

column_name: str = 'P_Short'

# You can use it like this:
num_unique_sessions: int = all_sessions_laps_time_bin_df.session_name.nunique(dropna=True) # number of unique sessions, ignoring the NA entries
num_unique_time_bins: int = all_sessions_laps_time_bin_df.time_bin_size.nunique(dropna=True)
_laps_histogram_out = plot_stacked_histograms(all_sessions_laps_time_bin_df, 'Laps', f'{num_unique_sessions} Sessions', f"{num_unique_time_bins} tbin sizes", column_name=column_name)

fig_to_clipboard(_laps_histogram_out.figures[0])

num_unique_sessions: int = all_sessions_ripple_time_bin_df.session_name.nunique(dropna=True) # number of unique sessions, ignoring the NA entries
num_unique_time_bins: int = all_sessions_ripple_time_bin_df.time_bin_size.nunique(dropna=True)
_ripple_histogram_out = plot_stacked_histograms(all_sessions_ripple_time_bin_df, 'Ripples', f'{num_unique_sessions} Sessions', f"{num_unique_time_bins} tbin sizes", column_name=column_name)



In [ ]:
all_sessions_ripple_time_bin_df['time_bin_size'].unique()

In [ ]:
# active_time_bin_size: float = 0.072 # 0.058
# active_time_bin_size: float = 0.086
# active_time_bin_size: float = 0.1 # looks the most bimodal with as little of an intermediate value as possible.
active_time_bin_size: float = 0.13444444 # looks the most bimodal with as little of an intermediate value as possible.
_single_time_bin_ripple_histogram_out = plot_stacked_histograms(all_sessions_ripple_time_bin_df[np.isclose(all_sessions_ripple_time_bin_df['time_bin_size'], active_time_bin_size)], 'Ripples', f'{num_unique_sessions} Sessions', f"tbin: {active_time_bin_size:0.3f}s", column_name=column_name)
fig_to_clipboard(_single_time_bin_ripple_histogram_out.figures[0], bbox_inches='tight')


In [ ]:
fig_to_clipboard(_ripple_histogram_out.figures[0])

In [ ]:
_laps_histogram_out.figures[0]

figures_folder

figures_folder

# 2024-03-28 - AcrossSessionTable (PhoDibaPaper2023 formats) .h5 and figure exports

In [ ]:
from pyphoplacecellanalysis.SpecificResults.AcrossSessionResults import AcrossSessionTables
from pyphoplacecellanalysis.SpecificResults.AcrossSessionResults import AcrossSessionsVisualizations
from pyphocorehelpers.DataStructure.RenderPlots.MatplotLibRenderPlots import MatplotlibRenderPlots


neuron_identities_table, long_short_fr_indicies_analysis_table, neuron_replay_stats_table = AcrossSessionTables.build_all_known_tables(included_session_contexts, included_h5_paths, should_restore_native_column_types=True)
num_sessions: int = len(long_short_fr_indicies_analysis_table['session_uid'].unique())
print(f'num_sessions: {num_sessions}')

long_short_fr_indicies_analysis_table


def _save_matplotlib_fig(matplotlib_output_container: MatplotlibRenderPlots):

    a_fig_context = matplotlib_output_container.context
    assert len(matplotlib_output_container.saved_figures) == 1
    a_saved_fig_path = matplotlib_output_container.saved_figures[0][0]
    assert a_saved_fig_path.exists()

    if neptuner_run is not None:
        a_full_figure_path_key: str = a_fig_context.get_description(separator='/', include_property_names=True, key_value_separator=':') # .replace(' ', '_')
        # a_full_figure_path_key: str = a_fig_context.get_description(separator=':', include_property_names=True, key_value_separator='|')
        print(f'a_full_figure_path_key: "{a_full_figure_path_key}"')
        # neptuner_run['outputs']['figures'][f"{a_full_figure_path_key}"].upload(a_fig)
        neptuner_run['outputs']['figures'][f"{a_full_figure_path_key}"].upload(a_saved_fig_path.as_posix())
        # neptuner.figures[f"{a_full_figure_path_key}"].upload(a_fig)
        


In [ ]:
# matplotlib_configuration_update(is_interactive=True, backend='Qt5Agg')
from pyphocorehelpers.DataStructure.RenderPlots.MatplotLibRenderPlots import MatplotlibRenderPlots

matplotlib.use('Qt5Agg')
matplotlib_output_container: MatplotlibRenderPlots = AcrossSessionsVisualizations.across_sessions_firing_rate_index_figure(long_short_fr_indicies_analysis_results=long_short_fr_indicies_analysis_table, num_sessions=num_sessions)

In [ ]:
# graphics_output_dict.figures[0]
# graphics_output_dict.context
_save_matplotlib_fig(matplotlib_output_container)

In [ ]:
graphics_output_dict.saved_figures[0][0] #.plot_data['saved_figures']

In [ ]:
copy_image_to_clipboard(graphics_output_dict['figures'][0])

In [ ]:
neptuner.stop()

## 2024-07-08 - Single Session Plotting


In [ ]:
csv_path = Path(r"K:\scratch\collected_outputs\2024-07-05-kdiba_gor01_two_2006-6-07_16-40-19__withNewKamranExportedReplays-(ripple_marginals_df).csv").resolve()
assert csv_path.exists()

ripple_df = pd.read_csv(csv_path)
ripple_df


In [ ]:
# from Spike3D.PendingNotebookCode import plot_stacked_histograms

# You can use it like this:'long_best_dir_simple_pearsonr'
_out1: "MatplotlibRenderPlots" = plot_histograms_across_sessions(data_type='Ripples', session_spec='All Sessions', data_results_df=ripple_df, time_bin_duration_str="20 ms")

In [ ]:
from pyphoplacecellanalysis.Pho2D.plotly.Extensions.plotly_helpers import plotly_pre_post_delta_scatter

# data_results_df: pd.DataFrame = deepcopy(all_sessions_laps_df) # all_sessions_laps_time_bin_df
# data_results_df: pd.DataFrame = deepcopy(ripple_df[['P_LR', 'P_RL', 'P_Long', 'P_Short', 'ripple_start_t', 'delta_aligned_start_t', 'time_bin_size']]).infer_objects()
data_results_df: pd.DataFrame = deepcopy(ripple_df[['P_Short','delta_aligned_start_t', 'time_bin_size']]).infer_objects()
data_results_df

In [ ]:
print(list(data_results_df.columns)) # ['Unnamed: 0', 'P_LR', 'P_RL', 'P_Long', 'P_Short', 'ripple_idx', 'ripple_start_t', 'session_name', 'delta_aligned_start_t', 'time_bin_size']
['P_LR', 'P_RL', 'P_Long', 'P_Short', 'ripple_start_t', 'delta_aligned_start_t', 'time_bin_size']


In [ ]:
# histogram_bins = 'auto'
histogram_bins: int = 25
new_ripple_fig, new_ripple_fig_context = plotly_pre_post_delta_scatter(data_results_df=data_results_df, out_scatter_fig=None, histogram_bins=histogram_bins, px_scatter_kwargs=dict(title='Ripple'), histogram_variable_name='P_Short')
new_ripple_fig


# new_laps_fig = new_laps_fig.update_layout(fig_size_kwargs, 
#     xaxis_title="X Axis Title",
#     yaxis_title="Y Axis Title",
#     legend_title="Legend Title",
#     font=dict(
#         family="Courier New, monospace",
#         size=18,
#         color="RebeccaPurple"
#     ),
# )
# Update x-axis labels
# new_laps_fig.update_xaxes(title_text="Num Time Bins", row=1, col=1)
# new_laps_fig.update_xaxes(title_text="Delta-aligned Event Time (seconds)", row=1, col=2)
# new_laps_fig.update_xaxes(title_text="Num Time Bins", row=1, col=3)


_extras_output_dict = {}
_extras_output_dict["y_mid_line"] = new_ripple_fig.add_hline(y=0.5, line=dict(color="rgba(0.8,0.8,0.8,.75)", width=2), row='all', col='all')

new_ripple_fig



# # Update layout to add a title to the legend
# new_fig_ripples.update_layout(
#     legend_title_text='Is User Selected'  # Add a title to the legend
# )

# fig_to_clipboard(new_fig_ripples, **fig_size_kwargs)

# new_laps_fig_context: IdentifyingContext = new_laps_fig_context.adding_context_if_missing(epoch='withNewKamranExportedReplays', num_sessions=num_sessions, plot_type='scatter+hist', comparison='pre-post-delta', variable_name=variable_name)
# figure_out_paths = save_plotly(a_fig=new_laps_fig, a_fig_context=new_laps_fig_context)
# new_laps_fig